# Mesures quantitatives d'inflation et perception médiatique 
## Projet Python pour la Data-science

### Auteurs : Lise Marchal, Raphaël Pereira et Raphaël Zambélli--Palacio

Ce notebook a pour objectif de présenter les travaux de recherche effectués dans le cadre du cours de Projet Python pour la data-science de la 2A ENSAE.

## Introduction

Ces dernières années, la France, comme de nombreux autres pays, a été confrontée à une crise inflationniste marquée, liée à divers facteurs économiques et géopolitiques. Durant cette période, le sujet de l'inflation et du pouvoir d'achat a été au coeur de nombreux débats et articles dans les médias. Alors que la hausse des prix ralentit actuellement, les débats sur l'inflation et ses implications continuent d'occuper une place  dans les médias et les discussions politiques mais plus secondaire qu'auparavant. Cette situation nous invite à interroger une possible relation entre l'évolution réelle de l'inflation et la manière dont ce phénomène est traité dans les médias.

Une étude récente de la Banque de France, intitulée "Utiliser la presse pour construire un nouvel indicateur de perception d’inflation en France" (Document de travail n°921, 2023, https://www.banque-france.fr/system/files/2023-09/wp921.pdf), explore comment les données textuelles issues des médias peuvent être utilisées pour mesurer la perception publique de l’inflation. En combinant des données de presse et des approches quantitatives, cette recherche propose un nouvel indicateur capable de refléter la sensibilité des médias à ce sujet. Inspirés par cette méthodologie, nous avons cherché à appliquer une approche similaire à un contexte historique en examinant la relation entre taux d’inflation et couverture médiatique aux États-Unis entre 1919 et 1963.

Notre projet vise à répondre à la question suivante : "Les périodes caractérisées par un taux d'inflation élevé coïncident-elles avec celles d’un traitement médiatique accru de cette thématique ?" Pour ce faire, nous nous sommes appuyés sur une base de données complète fournie par la Bibliothèque du Congrès américain, recensant les journaux nationaux et locaux publiés aux USA entre 1919 et 1963. Ce corpus, totalisant plus de 20 Go de données, offre une opportunité unique d’analyser les tendances historiques de la médiatisation de l'inflation aux États-Unis.

Dans un premier temps, nous avons analysé les données économiques contemporaines pour établir les périodes de forte inflation aux États-Unis. Nous avons ensuite collecté et nettoyé les données textuelles afin d’identifier les expression liées à l’inflation dans le corpus. Cette analyse a permis de mettre en correspondance les tendances médiatiques et économiques grâce à des méthodes quantitatives et des visualisations. Enfin, nous avons interprété les résultats pour évaluer les corrélations et les éventuels décalages temporels entre l'inflation réelle et sa médiatisation.

Les résultats préliminaires suggèrent une forte corrélation entre les deux phénomènes, bien que des variations importantes existent selon les périodes et les contextes économiques. Ces conclusions ouvrent des perspectives intéressantes pour mieux comprendre l'interaction entre la réalité économique et son traitement médiatique.


### Problématique : Les périodes caractérisées par un taux d'inflation élevé coïcident-elles avec celles de traitement médiatique accru de cette thématique ?




## Sommaire


- [Introduction](#introduction)

- [1- Statistiques descriptives des mesures d'inflation sur la période](#1-statistiques-descriptives-des-mesures-dinflation-sur-la-periode)
  - [1.1- Récupération des données d'inflation de la FED de Saint-Louis](#11-recuperation-des-donnees-dinflation-de-la-fed-de-saint-louis)
  - [1.2- Traitement des données sur l'inflation](#12-traitement-des-donnees-sur-linflation)

- [2- Analyse de fréquence sur le corpus de presse](#2-analyse-de-frequence-sur-le-corpus-de-presse)
  - [2.1- Récupération et formatage des dataframes](#21-recuperation-et-formatage-des-dataframes)
  - [2.2- Sélection des termes lexicaux](#22-selection-des-termes-lexicaux)
  - [2.3- Visualisations des fréquences](#23-visualisations-des-frequences)

- [3- Comparaisons de l'inflation mesurée et des fréquences](#3-comparaisons-de-linflation-mesuree-et-des-frequences)
  - [3.1- Analyse agrégée](#31-analyse-agregee)
  - [3.2- Prolongements](#32-prolongements)

- [4- Modélisation](#4-modelisation)
  - [4.1- Régression linéaire](#41-regression-lineaire)
  - [4.2- Analyse de sentiments](#42-analyse-de-sentiments)

In [238]:
# Imports:

import os
from dotenv import load_dotenv

import requests

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import plotly
import plotly.express as px
import plotly.io as pio
import plotly.graph_objects as go

from scipy.stats import pearsonr, kendalltau, spearmanr, chi2_contingency, chi2, pointbiserialr
import statsmodels.api as sm

import nltk
nltk.download("stopwords")
nltk.download("wordnet")
from nltk.corpus import stopwords
import string
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\lisem\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\lisem\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Gestion des fichiers avec SSP Cloud

In [239]:
import s3fs
import os

load_dotenv()
fs = s3fs.S3FileSystem(
    client_kwargs={'endpoint_url': 'https://'+'minio.lab.sspcloud.fr'},
    key = os.environ["AWS_ACCESS_KEY_ID"], 
    secret = os.environ["AWS_SECRET_ACCESS_KEY"], 
    token = os.environ["AWS_SESSION_TOKEN"])

MY_BUCKET = "rapamel"
fs.ls(MY_BUCKET)
path=f"{MY_BUCKET}/diffusion/ProjetDataScienceInflation"

<a id="1-statistiques-descriptives-des-mesures-dinflation-sur-la-periode"></a>

# 1- Statistiques descriptives des mesures d'inflation sur la période

<a id="#11-recuperation-des-donnees-dinflation-de-la-fed-de-saint-louis"></a>

## 1.1- Récupération des données d'inflation de la FED de Saint-Louis

<a id="111-utilisation-de-lapi-de-la-fred"></a>

### 1.1.1- Utilisation de l'API de la FRED:



La Fed de Saint-Louis met à disposition via son API de nombreuses bases de données d'indicateurs macroéconomiques. Elle offre notamment des séries temporelles couvrant la quasi totalité du XXème siècle ce qui est particulièrement intéressant pour notre projet. En effet, les articles de presse après 1963 ne sont plus en libre accès ce qui a nécessité de se concentrer sur la presse publiée pendant la première moitié du XXème siècle et donc de trouver des séries temporelles d'inflation mesurée sur cette période. Par ailleurs, parmi les nombreuses mesures d'inflation disponibles (ex : inflation sous-jacente, , indices de coûts etc.), nous avons retenu une série assez générale: "Consumer Price Index for All Urban Consumers: All Items in U.S. City Average" ("CPIAUCNS").

In [240]:
# Création de l'URL permettant d'accéder à la série choisie

load_dotenv()
api_root="https://api.stlouisfed.org/fred/series/observations"
series_id="CPIAUCNS"
api_key=os.getenv("FREDToken") # Récupération de la clé d'API dans le fichier .env
file_type="json"

url_api = (
    f"{api_root}?"
    + f"series_id={series_id}&"
    + f"api_key={api_key}&"
    + f"file_type={file_type}"
)

In [241]:
# Lancement de la requête avec l'url créé

req = requests.get(url_api)
wb = req.json()

### 1.1.2- Formatage des données

#### Création et première exploration du dataframe

In [242]:
# Création d'un dataframe à partir du fichier json

CPI_Urban=pd.json_normalize(wb["observations"]) 

In [243]:
CPI_Urban.head()

realtime_start realtime_end        date  value
0     2024-12-12   2024-12-12  1913-01-01  9.800
1     2024-12-12   2024-12-12  1913-02-01  9.800
2     2024-12-12   2024-12-12  1913-03-01  9.800
3     2024-12-12   2024-12-12  1913-04-01  9.800
4     2024-12-12   2024-12-12  1913-05-01  9.700

In [244]:
# Sélection des colonnes utiles: date et value
CPI_Urban = CPI_Urban[["date", "value"]]


In [245]:
# Infos générales (1)
CPI_Urban.axes

[RangeIndex(start=0, stop=1343, step=1),
 Index(['date', 'value'], dtype='object')]

In [246]:
# Infos générales (2)
CPI_Urban.dtypes

date     object
value    object
dtype: object

#### Traitement des indices d'inflation

In [247]:
# Conversion du type object vers le type numérique
CPI_Urban['value'] = pd.to_numeric(CPI_Urban['value'], errors='coerce')


#### Traitement des dates

In [248]:
# Conversion en types dates et création des variables années et mois
CPI_Urban['date'] = pd.to_datetime(CPI_Urban['date'])
CPI_Urban['year'] = CPI_Urban['date'].dt.year
CPI_Urban['month'] = CPI_Urban['date'].dt.month

CPI_Urban.head()

date  value  year  month
0 1913-01-01    9.8  1913      1
1 1913-02-01    9.8  1913      2
2 1913-03-01    9.8  1913      3
3 1913-04-01    9.8  1913      4
4 1913-05-01    9.7  1913      5

#### Création de la variable pourcentage d'inflation annuelle ("inf_an") : 

Le jeu de données se présente sous la forme d'indices avec une base 100 en 1983. Le choix a cependant été fait de réaliser l'analyse sur des pourcentages d'inflation. On crée donc la variable inf_an, qui correspond au pourcentage d'inflation calculé par rapport au niveau de l'indice de prix douze mois plus tôt. 
$$
    \frac{indice_t - indice_{t-12}}{indice_{t-12}}*100
$$

On relèvera cependant une limite : il n'est pas idéal d'avoir la date de la base 100 postérieure à la période étudiée ouisque le panier de biens et services considéré peut s'avérer moins pertinent à des dates très antérieures.  

In [249]:
# Inflation annuelle: ((indice/indice 12 mois auparavant)-1)*100
CPI_Urban['inf_an']=((CPI_Urban['value']-CPI_Urban['value'].shift(12))/CPI_Urban['value'].shift(12))*100
CPI_Urban.head(20)

date  value  year  month    inf_an
0  1913-01-01    9.8  1913      1       NaN
1  1913-02-01    9.8  1913      2       NaN
2  1913-03-01    9.8  1913      3       NaN
3  1913-04-01    9.8  1913      4       NaN
4  1913-05-01    9.7  1913      5       NaN
5  1913-06-01    9.8  1913      6       NaN
6  1913-07-01    9.9  1913      7       NaN
7  1913-08-01    9.9  1913      8       NaN
8  1913-09-01   10.0  1913      9       NaN
9  1913-10-01   10.0  1913     10       NaN
10 1913-11-01   10.1  1913     11       NaN
11 1913-12-01   10.0  1913     12       NaN
12 1914-01-01   10.0  1914      1  2.040816
13 1914-02-01    9.9  1914      2  1.020408
14 1914-03-01    9.9  1914      3  1.020408
15 1914-04-01    9.8  1914      4  0.000000
16 1914-05-01    9.9  1914      5  2.061856
17 1914-06-01    9.9  1914      6  1.020408
18 1914-07-01   10.0  1914      7  1.010101
19 1914-08-01   10.2  1914      8  3.030303

#### Création d'un sous-tableau de la période considérée (1919-1962)

In [250]:
CPI_sub = CPI_Urban[(CPI_Urban['year'] > 1918) & (CPI_Urban['year'] < 1963)]
CPI_sub.head()


date  value  year  month     inf_an
72 1919-01-01   16.5  1919      1  17.857143
73 1919-02-01   16.2  1919      2  14.893617
74 1919-03-01   16.4  1919      3  17.142857
75 1919-04-01   16.7  1919      4  17.605634
76 1919-05-01   16.9  1919      5  16.551724

In [251]:
CPI_sub.tail()

date  value  year  month    inf_an
595 1962-08-01   30.3  1962      8  1.337793
596 1962-09-01   30.4  1962      9  1.333333
597 1962-10-01   30.4  1962     10  1.333333
598 1962-11-01   30.4  1962     11  1.333333
599 1962-12-01   30.4  1962     12  1.333333

<a id="12-traitement-des-donnees-sur-linflation"></a>


## 1.2- Traitement des données sur l'inflation

<a id="121-premieres-statistiques-descriptives"></a>


### 1.2.1- Premières statistiques descriptives sur l'inflation pendant la période

#### Premières statistiques sur l'ensemble du dataframe (1919-1962)

In [252]:
CPI_sub['inf_an'].describe()

count    528.000000
mean       1.781563
std        6.051345
min      -15.789474
25%       -0.700532
50%        1.355948
75%        3.361353
max       23.668639
Name: inf_an, dtype: float64

Grâce à ces premières statistiques, on peut déjà constater que l'inflation annuelle moyenne entre 1919 et 1962 est positive. Elle est de plus relativement proche des cibles d'inflation contemporaines (environ 1.8%). La volatilité est élevée, l'écart-type s'élevant à 6.1%. Sur la période considérée le pourcentage d'inflation minimum s'est élevé à -15.8%, tandis que le pourcentage d'inflation maximum a culminé à 23.7%. Ces niveaux sont respectivement bien inférieurs et supérieurs à ceux observés dans les décennies plus récentes. Enfin, le pourcentage d'inflation annuel médian est inférieur au pourcentage d'inflation moyenne ce qui indique une distribution plus dispersée vers le haut. 

#### Figure 1: Evolution du pourcentage d'inflation annuelle par mois sur l'ensemble de la période

In [253]:
# Création d'une fonction de base pour la création de graphiques en courbe

def line_graph (df, abs, ord, titre, x_title, x_format, y_title, val_rem):
    """
    Fonction traçant un graphique en courbe interactif.
    ==================================================
    Paramètres:
    ==================================================
    df: dataframe d'où sont issues les données
    abs: série sur l'axe des abcisses
    ord: série sur l'axe des ordonnées
    titre: titre du graphique
    x_title: nom de l'axe des abcisses
    y_title: nom de l'axe des ordonnées
    val_rem: booléen indiquant si l'on souhaite ou non l'affichage des valeurs remarquables (0, moyenne, médiane)
    """

    # Création du graphique
    graph = px.line(
        df, 
        x=abs, 
        y=ord, 
        title=titre,
        labels={abs: x_title, ord:y_title}
    )
    # Légende et format des axes
    graph.update_xaxes(title=x_title, tickformat=x_format)
    graph.update_yaxes(title=y_title)

    # Style du graphique
    graph.update_layout(template="plotly_dark")

    # Mise en évidence des valeurs remarquables (moyenne et médiane)
    if val_rem==True:
        mean=df[ord].mean()
        median=df[ord].median()
        
        graph.add_hline(y=mean, line_dash="dot", line_color="yellow", annotation_text="Moyenne", annotation_position="top left", annotation_font_color="yellow")
        graph.add_hline(y=median, line_dash="dot", line_color="white", annotation_text="Médiane", annotation_position="bottom right", annotation_font_color="white")
        graph.add_hline(y=0, line_color="red")

    graph.show(config={"scrollZoom": True, "displayModeBar": True})

    
    

In [254]:
line_graph (
    CPI_sub, 
    "date", 
    "inf_an", 
    "Figure 1: Pourcentage d'inflation annuelle de 1919 à 1962", 
    "Date", 
    "%m-%Y", 
    "Inflation (%)",
    True
)

On observe une **première période de très forte inflation** dans l'immédiat après-guerre. L'inflation est en effet comprise entre 13.5% et 23,7%, niveau maximum sur l'ensemble de notre période d'étude, atteint en juin 1920. Cette période est suivie de la **première période de déflation**, de janvier 1921 à février 1923. La déflation la plus forte de la période a lieu en juin 1921 (-15.8%). Après une relative stabilité dans les années 20, la crise des années 30 engendre une **deuxième période de déflation**, de mai 1930 à novembre 1933, l'inflation restant autour de -9.5% pendant deux ans. L'inflation reste ensuite faible jusqu'à la Seconde Guerre mondiale. Celle-ci se caractérise par une **deuxième période d'inflation**, avec un pic à 13.2% en mai 1942. Cependant, cette période est assez courte, la moyenn'inflation retrouvant son niveau moyen de longue période dès le début de 1944. L'après-guerre constitue en revanche une **troisième période de forte inflation**, avec un pic à 19.7%. La fin de la période, notamment à partir de 1952, se caractérise elle par un **stabilisation de l'inflation à des niveaux faibles**, autour de la médiane à 1.4%. 

<a id="122-identification-de-periodes-dinteret"></a>


### 1.2.2- Identification de périodes d'intérêt

#### Identification des périodes d'inflation négative

##### Création d'une indicatrice prenant la valeur 1 si l'inflation est négative et 0 sinon

In [255]:
# Création d'une indicatrice inf_neg qui prend la valeur 1 si l'inflation est négative et 0 sinon
CPI_sub.loc[:,'inf_neg']=0
CPI_sub.loc[CPI_sub['inf_an'] < 0, 'inf_neg'] = 1
CPI_sub.head(30)

C:\Users\lisem\AppData\Local\Temp\ipykernel_28808\1604323234.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



date  value  year  month     inf_an  inf_neg
72  1919-01-01   16.5  1919      1  17.857143        0
73  1919-02-01   16.2  1919      2  14.893617        0
74  1919-03-01   16.4  1919      3  17.142857        0
75  1919-04-01   16.7  1919      4  17.605634        0
76  1919-05-01   16.9  1919      5  16.551724        0
77  1919-06-01   16.9  1919      6  14.965986        0
78  1919-07-01   17.4  1919      7  15.231788        0
79  1919-08-01   17.7  1919      8  14.935065        0
80  1919-09-01   17.8  1919      9  13.375796        0
81  1919-10-01   18.1  1919     10  13.125000        0
82  1919-11-01   18.5  1919     11  13.496933        0
83  1919-12-01   18.9  1919     12  14.545455        0
84  1920-01-01   19.3  1920      1  16.969697        0
85  1920-02-01   19.5  1920      2  20.370370        0
86  1920-03-01   19.7  1920      3  20.121951        0
87  1920-04-01   20.3  1920      4  21.556886        0
88  1920-05-01   20.6  1920      5  21.893491        0
89  1920-06-01   20.9  1920      6  23.668639        0
90  1920-07-01   20.8  1920      7  19.540230        0
91  1920-08-01   20.3  1920      8  14.689266        0
92  1920-09-01   20.0  1920      9  12.359551        0
93  1920-10-01   19.9  1920     10   9.944751        0
94  1920-11-01   19.8  1920     11   7.027027        0
95  1920-12-01   19.4  1920     12   2.645503        0
96  1921-01-01   19.0  1921      1  -1.554404        1
97  1921-02-01   18.4  1921      2  -5.641026        1
98  1921-03-01   18.3  1921      3  -7.106599        1
99  1921-04-01   18.1  1921      4 -10.837438        1
100 1921-05-01   17.7  1921      5 -14.077670        1
101 1921-06-01   17.6  1921      6 -15.789474        1

##### Quelques statistiques sur les périodes d'inflation négative

In [256]:
CPI_sub[CPI_sub['inf_neg'] == 1]['inf_an'].describe()

count    156.000000
mean      -4.190409
std        4.039146
min      -15.789474
25%       -7.702932
50%       -2.240914
75%       -1.048073
max       -0.371747
Name: inf_an, dtype: float64

On a donc 156 mois de déflation contre 372 mois d'inflation positive sur la période 1919-1962. Les mois de déflation sont largement concentrés avant la Seconde Guerre mondiale (Cf. Figure 2). La moyenne du pourcentage d'inflation sur ces périodes de déflations est assez basse (-4.2%), significativement inférieure à la médiane (-2.2%), du fait du nombre important d'observations très négatives. 

##### Figure 2: Représentation des périodes d'inflation négative de 1919 à 1962

In [257]:
graph=px.bar(
            CPI_sub, 
            x='date', 
            y='inf_neg', 
            title="Figure 2: Représentation des périodes d'inflation négative de 1919 à 1962",
            labels={'date': 'Date', 'inf_neg':'Inflation négative'},
            
        )

graph.update_layout(template="plotly_dark")

graph.show(config={"scrollZoom": True, "displayModeBar": True})

#### Identification des périodes d'accélération et de décélération

Pour mesurer l'accélération et la décélération de l'inflation, le choix a été fait de s'intéresser à la différence entre l'inflation observée un mois donné et le pourcentage d'inflation douze mois auparavant.
En raison du nombre important de valeurs négatives, l'échelle logarithmique n'a pas été retenue malgré les avantages qu'elle aurait eu, notamment en raison des forts pourcentages d'évolution. Le choix de calculer des taux de croissance pose néanmoins le problème des valeurs d'inflation nulles dues à des arrondis. On les remplace par les moyennes des valeurs immédiatement précédente et suivante pour lisser la représentation lorsqu'elles sont isolées, sinon par les valeurs non nulles immédiatement précédente ou suivante. 

##### Création de la variable acceleration_12 (pourcentage d'accélération)

In [258]:
# Création du pourcentage d'évolution de l'inflation
CPI_sub.loc[:, 'acceleration_12'] = (CPI_sub.loc[:,'inf_an']/CPI_sub.loc[:,'inf_an'].shift(12) - 1)*100 
CPI_sub.head(30)


C:\Users\lisem\AppData\Local\Temp\ipykernel_28808\750671830.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



date  value  year  month     inf_an  inf_neg  acceleration_12
72  1919-01-01   16.5  1919      1  17.857143        0              NaN
73  1919-02-01   16.2  1919      2  14.893617        0              NaN
74  1919-03-01   16.4  1919      3  17.142857        0              NaN
75  1919-04-01   16.7  1919      4  17.605634        0              NaN
76  1919-05-01   16.9  1919      5  16.551724        0              NaN
77  1919-06-01   16.9  1919      6  14.965986        0              NaN
78  1919-07-01   17.4  1919      7  15.231788        0              NaN
79  1919-08-01   17.7  1919      8  14.935065        0              NaN
80  1919-09-01   17.8  1919      9  13.375796        0              NaN
81  1919-10-01   18.1  1919     10  13.125000        0              NaN
82  1919-11-01   18.5  1919     11  13.496933        0              NaN
83  1919-12-01   18.9  1919     12  14.545455        0              NaN
84  1920-01-01   19.3  1920      1  16.969697        0        -4.969697
85  1920-02-01   19.5  1920      2  20.370370        0        36.772487
86  1920-03-01   19.7  1920      3  20.121951        0        17.378049
87  1920-04-01   20.3  1920      4  21.556886        0        22.443114
88  1920-05-01   20.6  1920      5  21.893491        0        32.273176
89  1920-06-01   20.9  1920      6  23.668639        0        58.149543
90  1920-07-01   20.8  1920      7  19.540230        0        28.285857
91  1920-08-01   20.3  1920      8  14.689266        0        -1.645787
92  1920-09-01   20.0  1920      9  12.359551        0        -7.597646
93  1920-10-01   19.9  1920     10   9.944751        0       -24.230466
94  1920-11-01   19.8  1920     11   7.027027        0       -47.936118
95  1920-12-01   19.4  1920     12   2.645503        0       -81.812169
96  1921-01-01   19.0  1921      1  -1.554404        1      -109.159882
97  1921-02-01   18.4  1921      2  -5.641026        1      -127.692308
98  1921-03-01   18.3  1921      3  -7.106599        1      -135.317643
99  1921-04-01   18.1  1921      4 -10.837438        1      -150.273673
100 1921-05-01   17.7  1921      5 -14.077670        1      -164.300708
101 1921-06-01   17.6  1921      6 -15.789474        1      -166.710526

In [259]:
# Traitement des pourcentages d'évolution infinis

# On le fait un nb arbitraire de fois pour traiter les cas de 3,4,5,6 valeurs infinies se suivant. 
# On ne fait pas une boucle while par exemple sur la moyenne pour éviter les boucles infinies

for i in range(5):
    # traitement des valeurs infinies isolées: remplacement par la moyenne entre la valeur précédente et la valeur suivante
    CPI_sub.loc[
        abs(CPI_sub["acceleration_12"]) == np.inf,
        "acceleration_12"
    ] = (CPI_sub["acceleration_12"].shift(1) + CPI_sub["acceleration_12"].shift(-1)) / 2
    #traitement des valeurs infinies suivies de valeurs infinies: remplacement par la valeur précédente
    CPI_sub.loc[
        (abs(CPI_sub["acceleration_12"]) == np.inf) & (abs(CPI_sub["acceleration_12"].shift(-1)) == np.inf),
        "acceleration_12"
    ] = CPI_sub["acceleration_12"].shift(1)

    #traitement des valeurs infinies précédées de valeurs infinies: remplacement par la valeur suivante
    CPI_sub.loc[
        (abs(CPI_sub["acceleration_12"]) == np.inf) & (abs(CPI_sub["acceleration_12"].shift(1)) == np.inf),
        "acceleration_12"
    ] = CPI_sub["acceleration_12"].shift(-1)

CPI_sub.head(20)



date  value  year  month     inf_an  inf_neg  acceleration_12
72 1919-01-01   16.5  1919      1  17.857143        0              NaN
73 1919-02-01   16.2  1919      2  14.893617        0              NaN
74 1919-03-01   16.4  1919      3  17.142857        0              NaN
75 1919-04-01   16.7  1919      4  17.605634        0              NaN
76 1919-05-01   16.9  1919      5  16.551724        0              NaN
77 1919-06-01   16.9  1919      6  14.965986        0              NaN
78 1919-07-01   17.4  1919      7  15.231788        0              NaN
79 1919-08-01   17.7  1919      8  14.935065        0              NaN
80 1919-09-01   17.8  1919      9  13.375796        0              NaN
81 1919-10-01   18.1  1919     10  13.125000        0              NaN
82 1919-11-01   18.5  1919     11  13.496933        0              NaN
83 1919-12-01   18.9  1919     12  14.545455        0              NaN
84 1920-01-01   19.3  1920      1  16.969697        0        -4.969697
85 1920-02-01   19.5  1920      2  20.370370        0        36.772487
86 1920-03-01   19.7  1920      3  20.121951        0        17.378049
87 1920-04-01   20.3  1920      4  21.556886        0        22.443114
88 1920-05-01   20.6  1920      5  21.893491        0        32.273176
89 1920-06-01   20.9  1920      6  23.668639        0        58.149543
90 1920-07-01   20.8  1920      7  19.540230        0        28.285857
91 1920-08-01   20.3  1920      8  14.689266        0        -1.645787

##### Figure 3: Pourcentage d'accélération de l'inflation annuelle par mois de 1920 à 1962

In [260]:
line_graph (
    CPI_sub, 
    "date", 
    "acceleration_12", 
    "Figure 3: Pourcentage d'accélération de l'inflation annuelle par mois de 1920 à 1962", 
    "Date", 
    "%m-%Y", 
    "Accélération (%)",
    False
)

On constate que les périodes d'accélération et de décélération sont souvent les mêmes, correspondant en fait à quatre pics de volatilité, avec des pourcentages d'accélération qui dépassent le seuil de 1000% en valeur absolue : autour de 1931, de 1941, de 1947 et de 1951. Ils correspondent donc tous à des périodes de forte inflation ou de déflation accentuée.

<a id="2-analyse-de-frequence-sur-le-corpus-de-presse"></a>


# 2- Analyse de fréquence sur le corpus de presse

<a id="21-recuperation-et-formatage-des-dataframes"></a>


## 2.1- Récupération et formatage des dataframes de fréquence

**Note**: En raison du temps d'exécution important nécessaire à la réalisation des fichiers csv. de fréquence d'occurence des termes liés au champs lexical de l'inflation, ceux-ci sont générés à part et seulement importés ici.

Ce notebok, nommé "Analyse_NLP_frequentielle", est un codebook annexe contenant toutes les fonctions nécessaires à cette étape du code. Il permet de récupérer un dictionnaire contenant pour chaque mois, le nombre d'articles ainsi que, pour chaque expression liée à l'inflation, le nombre d'articles sur le mois contenant l'expression.

Il est conseillé d'aller voir ce notebook car il permet de bien comprendre comment nous avons obtenu ces résultats. Comme son temps d'exécution est très conséquent, vous pouvez le tester sur une année seulement au lieu de tout le corpus, ce qui prend un temps raisonnable (environ 7 minutes). Pour plus de détails, aller voir le notebook en question.

**Choix des expressions**: Pour détecter quel article parle d'inflation, nous nous sommes inspirés de l'article de recherche fait par la Banque de France (https://www.banque-france.fr/system/files/2023-09/wp921.pdf) qui avait pour objectif de construire un indicateur d'inflation perçu en France à partir des articles de presse et de Tweeter. Dans un premier temps, ils ont élaboré une liste d'expressions pouvant être liée à l'inflation.

Leur méthode a été de prendre des mots assez large comme "price" ou encore "tabac" pour faire un premier filtre avant de faire un second filtrage à l'aide d'outils de classification supervisée.

Comme nous ne pensions pas faire de second filtrage, nous avons décidé de restreindre un peu les expressions choisies. On a tout de même gardé un éventail assez large, quitte à faire un tri dans les expressions que l'on analysera par la suite.

Une dernière différence par rapport aux choix des expressions est la présence de 2-gram et 3-gram. En effet, nous avons ajouté des expressions à 2 mots et 3 mots (comme "cost of living"), considérant qu'elles pourraient potentiellement apporter des informations.

NotaBene : Les expressions sont uniquement en minuscule, pour éviter de rater les articles parlant d'inflation mais dont le terme "Inflation" serait en majuscule, nous transformons le texte des articles en minuscule lors de l'analyse (voir le codebook annexe)

In [ ]:
def creer_dictionnaire_inflation():
    #Cette fonction renvoie un dictionnaire de n-gram relatifs à l'inflation et aux prix

    dictionnaire = {
        "1-gram": [
            "inflation", "disinflation", "inflationary", "deflation", "prices", "cost", "wages", "currency",
            "money", "devaluation","recession", "stagflation", "economy", "market", "increase", "decrease", "cpi"
        ],
        "2-gram": [
            "price level", "wage growth", "economic downturn", "monetary policy",
            "cost increase", "cost reduction", "inflation expectations", "market prices", "inflation rate",
            "interest rates", "price stability", "consumption basket", "purchasing power"
        ],
        "3-gram": [
            "consumer price index", "rise in prices", "fall in prices",
            "cost of living", "money supply growth",
            "central bank policy", "economic price adjustments"
        ]
    }
    return dictionnaire

dictionnaire_inflation = creer_dictionnaire_inflation()

 -->AJOUTER TEXTE SUR CHOIX ET BDD

<a id="211-creation-de-tables-par-decennie"></a>


### 2.1.1- Création de tables par décennie et d'une table sur toute la période

In [261]:
# Récupération des données dans un dictionnaire par décennie
dates=["1919_1929","1930_1939","1940_1949","1950_1959","1960_1963"]

df = {}

for date in dates: 
    url=(
        "frequences_data_"
        + f"{date}"
        +".csv"
    )
    
    df[f"freq_{date}"] = pd.read_csv(url)



In [262]:
# Création d'une table sur toute la période
freq_tot=pd.concat([df["freq_1919_1929"],df["freq_1930_1939"],df["freq_1940_1949"],df["freq_1950_1959"],df["freq_1960_1963"]])

In [263]:
# Affichage de toutes les colonnes et de toutes les lignes
pd.set_option('display.max_columns', None) 
pd.set_option('display.max_rows', None) 

<a id="211-creation-de-tables-par-decennie"></a>

### 2.1.1- Premières informations sur les données

In [264]:
freq_tot.head()

key  nbre_articles  inflation  disinflation  inflationary  deflation  \
0  1919-01         228632          3             0             0          3   
1  1919-02         195555          0             0             0          4   
2  1919-03         234087          3             0             0          3   
3  1919-04         245278          1             0             0          0   
4  1919-05         243206          3             0             0          1   

   prices  cost  wages  currency  money  devaluation  recession  stagflation  \
0    5359  8523   2040       292   9151            0         49            0   
1    4671  7521   1946       270   8202            2         59            0   
2    5284  8410   1969       408   9873            0         77            0   
3    5773  8771   2016       301   9725            0        127            0   
4    5014  8401   1567       269   9259            0         80            0   

   economy  market  increase  decrease  cpi  price level  wage growth  \
0      531    5859      6747       921  138           50            0   
1      468    4970      5128       620   94           45            0   
2      522    5786      5867       704  120           60            0   
3      527    6031      6198       689  100           77            0   
4      506    5768      5621       598   90           61            0   

   economic downturn  monetary policy  cost increase  cost reduction  \
0                  0                0              2               1   
1                  0                0              0               1   
2                  0                0              4               3   
3                  0                0              3               0   
4                  0                0              0               0   

   market prices  inflation rate  interest rates  price stability  \
0             79               0              36                2   
1             71               0              31                0   
2             83               0              47                0   
3            119               0              39                1   
4             55               0              22                0   

   consumption basket  purchasing power  consumer price index  rise in prices  \
0                   0                54                     0              11   
1                   0                43                     0              10   
2                   0                48                     0              10   
3                   0                55                     0               5   
4                   0                54                     0              10   

   fall in prices  cost of living  inflation expectations  \
0               9             396                       0   
1               7             339                       0   
2               2             362                       0   
3               8             267                       0   
4               4             275                       0   

   money supply growth  central bank policy  economic price adjustments  
0                    0                    0                           0  
1                    0                    0                           0  
2                    0                    0                           0  
3                    0                    0                           0  
4                    0                    0                           0

In [265]:
freq_tot.dtypes

key                           object
nbre_articles                  int64
inflation                      int64
disinflation                   int64
inflationary                   int64
deflation                      int64
prices                         int64
cost                           int64
wages                          int64
currency                       int64
money                          int64
devaluation                    int64
recession                      int64
stagflation                    int64
economy                        int64
market                         int64
increase                       int64
decrease                       int64
cpi                            int64
price level                    int64
wage growth                    int64
economic downturn              int64
monetary policy                int64
cost increase                  int64
cost reduction                 int64
market prices                  int64
inflation rate                 int64
i

In [266]:
# Formatage des dates

freq_tot = freq_tot.rename(columns={'key': 'date'}) # Renommage de la colonne 'key' en 'date'
freq_tot['date'] = pd.to_datetime(freq_tot['date'])
freq_tot['year'] = freq_tot['date'].dt.year
freq_tot['month'] = freq_tot['date'].dt.month

<a id="22-selection-des-termes-lexicaux"></a>

## 2.2- Sélection des termes du champ lexical de l'inflation et des prix les plus utilisés dans les articles 

On cherche à sélectionner les termes les plus utilisés pour permettre de produire une analyse plus pertinente et lisible.

In [267]:
# Listes utiles (1)

# Liste comprenant les colonnes autres que les termes du champ lexical de l'inflation
autres = ['date','year', 'month', 'nbre_articles']

In [268]:
# Affichage des statistiques descriptives pour les termes du champ lexical et classement par ordre décroissant des moyennes d'occurence
desc=freq_tot.drop(columns=autres).describe()
desc_transposed = desc.transpose()
desc_sorted = desc_transposed.sort_values(by="mean", ascending=False)
desc_sorted

count         mean          std    min      25%  \
cost                        540.0  2357.485185  2409.023489  141.0  1339.75   
money                       540.0  2099.877778  2528.900171  109.0   953.00   
increase                    540.0  1522.175926  1710.485732   66.0   723.50   
market                      540.0  1376.216667  1722.858584   68.0   582.50   
prices                      540.0  1267.101852  1575.630575   46.0   555.50   
wages                       540.0   363.744444   547.831950    7.0    99.00   
economy                     540.0   231.961111   191.772342   18.0   134.00   
decrease                    540.0   203.553704   279.939589    3.0    48.00   
currency                    540.0   105.787037   134.673180    0.0    30.00   
cost of living              540.0    78.190741   267.784511    0.0    11.00   
recession                   540.0    31.440741    38.719655    0.0     9.00   
purchasing power            540.0    24.703704    27.958377    0.0     6.00   
cpi                         540.0    20.737037    29.852347    0.0     6.00   
price level                 540.0    15.572222    19.437268    0.0     4.00   
interest rates              540.0    13.890741    14.949672    0.0     4.00   
market prices               540.0    13.494444    23.514216    0.0     3.00   
inflation                   540.0    10.162963    15.058184    0.0     2.00   
deflation                   540.0     6.857407    13.353480    0.0     1.00   
inflationary                540.0     5.948148     8.255492    0.0     0.00   
devaluation                 540.0     4.716667    14.371925    0.0     0.00   
rise in prices              540.0     3.014815     4.733311    0.0     0.00   
monetary policy             540.0     1.542593     7.271315    0.0     0.00   
fall in prices              540.0     1.059259     3.161134    0.0     0.00   
cost increase               540.0     1.018519     1.827341    0.0     0.00   
price stability             540.0     0.596296     1.484610    0.0     0.00   
cost reduction              540.0     0.359259     0.743935    0.0     0.00   
consumer price index        540.0     0.288889     0.727072    0.0     0.00   
economic downturn           540.0     0.055556     0.299453    0.0     0.00   
disinflation                540.0     0.024074     0.238607    0.0     0.00   
central bank policy         540.0     0.005556     0.074397    0.0     0.00   
money supply growth         540.0     0.001852     0.043033    0.0     0.00   
wage growth                 540.0     0.000000     0.000000    0.0     0.00   
stagflation                 540.0     0.000000     0.000000    0.0     0.00   
consumption basket          540.0     0.000000     0.000000    0.0     0.00   
inflation rate              540.0     0.000000     0.000000    0.0     0.00   
inflation expectations      540.0     0.000000     0.000000    0.0     0.00   
economic price adjustments  540.0     0.000000     0.000000    0.0     0.00   

                               50%      75%      max  
cost                        1682.0  2308.75  14471.0  
money                       1281.0  2106.50  11815.0  
increase                    1045.0  1439.75   9514.0  
market                       844.0  1262.50   7907.0  
prices                       854.5  1130.00   9411.0  
wages                        210.0   322.00   4011.0  
economy                      183.0   242.25   1303.0  
decrease                     113.0   212.00   1604.0  
currency                      53.0   111.00    750.0  
cost of living                19.0    45.25   4289.0  
recession                     21.0    37.00    427.0  
purchasing power              16.0    32.00    216.0  
cpi                           12.0    20.00    181.0  
price level                    9.5    18.00    173.0  
interest rates                 9.0    17.00     96.0  
market prices                  6.0    11.00    162.0  
inflation                      5.0    13.25    134.0  
deflation                      2.0 

On remarque que certains termes sont beaucoup plus utilisés que d'autres : *cost, money, increase, market, prices*, etc.
Pour certains comme *increase*, cela peut sûrement être dû à leur utilisation dans des contextes très différents. Pour d'autres, comme *price* ou *cost*, on peut considérer que cela donne une indication du traitement de thématiques liées à l'inflation. On peut envisager que ce thème soit plus traité par l'évocation des prix ou des coûts que par des termes plus spécifiques comme *deflation*, *inflationary* ou encore *money supply growth*.
Enfin, ceci peut aussi être lié à la base de données utilisée, même si le nombre important d'articles peut laisser supposer une certaine représentativité. 

In [269]:
# Listes utiles (2):

# Liste des termes les plus utilisés dans les articles
selected=desc_sorted.index[desc_sorted['mean']>10].to_list()

# Liste des colonnes du dataframe réduit
sub=autres+selected

# Liste des variables numériques
num=selected+['nbre_articles']



In [270]:
# Création d'un dataframe réduit
freq_sub=freq_tot[sub]
freq_sub.head()

date  year  month  nbre_articles  cost  money  increase  market  \
0 1919-01-01  1919      1         228632  8523   9151      6747    5859   
1 1919-02-01  1919      2         195555  7521   8202      5128    4970   
2 1919-03-01  1919      3         234087  8410   9873      5867    5786   
3 1919-04-01  1919      4         245278  8771   9725      6198    6031   
4 1919-05-01  1919      5         243206  8401   9259      5621    5768   

   prices  wages  economy  decrease  currency  cost of living  recession  \
0    5359   2040      531       921       292             396         49   
1    4671   1946      468       620       270             339         59   
2    5284   1969      522       704       408             362         77   
3    5773   2016      527       689       301             267        127   
4    5014   1567      506       598       269             275         80   

   purchasing power  cpi  price level  interest rates  market prices  \
0                54  138           50              36             79   
1                43   94           45              31             71   
2                48  120           60              47             83   
3                55  100           77              39            119   
4                54   90           61              22             55   

   inflation  
0          3  
1          0  
2          3  
3          1  
4          3

<a id="23-visualisations-des-frequences"></a>

## 2.3- Premières visualisations des fréquences d'occurence des termes liés à l'inflation 

In [271]:
# Création d'une fonction de base diagramme à barres empilées

def stacked_bar(df,abs,sections,titre,x_title,y_title, var_title):
    """
    Fonction traçant un diagramme à barres empilées.
    ==================================================
    Paramètres:
    ==================================================
    df: dataframe d'où sont issues les données
    abs: série sur l'axe des abcisses
    ord: sections découpant chaque barre
    titre: titre du graphique
    x_title: nom de l'axe des abcisses
    y_title: nom de l'axe des ordonnées
    var_title: nom des sections des barres
    """
    graph=px.bar(
            df, 
            x=abs, 
            y=sections, 
            title=titre,
            labels={abs: x_title, 'value':y_title, 'variable':var_title}
        )

    graph.update_layout(template="plotly_dark")

    graph.show(config={"scrollZoom": True, "displayModeBar": True})


<a id="introduction"></a>

### 2.3.1- Nombre d'occurences par mois des termes les plus utilisés dans le champ lexical de l'inflation

In [272]:
# Création d'un graphique représentant le nombre d'articles mentionnant les termes sélectionnés par année:

stacked_bar(
    freq_sub,
    'date',
    selected,
    "Figure 4: Nombre d'occurences par mois des termes liés à l'inflation de 1919 à 1962",
    "Date",
    "Nb occurences",
    "Mot"
)

On remarque que la base de données comprend un nombre d'articles beaucoup plus important dans les premières années, rendant le graphique peu lisible. Il est possible de zoomer pour avoir plus d'informations ou de se référer aux graphiques suivant coupant la période en deux selon l'ordre de grandeurs du nombre d'articles. 

In [273]:
stacked_bar(
    freq_sub[freq_sub['year']<1923],
    'date',
    selected,
    "Figure 4.1: Nombre d'occurences par mois des termes liés à l'inflation de 1919 à 1922",
    "Date",
    "Nb occurences",
    "Mot"
)

In [274]:
stacked_bar(
    freq_sub[freq_sub['year']>1923],
    'date',
    selected,
    "Figure 4.2: Nombre d'occurences par mois des termes liés l'inflation de 1923 à 1962",
    "Date",
    "Nb occurences",
    "Mot"
)

On constate bien la prévalence des termes *cost*, *money*, *increase*, *market* et *price*. On note également les très faibles occurences dans la deuxième moitié des années 50. Ceci s'explique par le nombre d'articles plus limité présent dans la base pour cette période, sans qu'aucune explication soit disponible. On veillera donc à ne pas sur-interpréter les résultats sur cette période. On peut également s'intéresser à une analyse en termes de proportion pour éviter une influence trop forte de la variable nombre d'articles.

<a id="introduction"></a>

### 2.3.2- Pourcentage d'articles par mois contenant les termes les plus utilisés dans le champ lexical de l'inflation 

In [275]:
# Créations des pourcentages

for col in selected:
    freq_sub.loc[:,f"{col}_rat"]=(freq_sub.loc[:,f"{col}"]/freq_sub.loc[:,'nbre_articles'])*100

freq_sub.head(2)

C:\Users\lisem\AppData\Local\Temp\ipykernel_28808\3701922892.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\lisem\AppData\Local\Temp\ipykernel_28808\3701922892.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\lisem\AppData\Local\Temp\ipykernel_28808\3701922892.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/panda

date  year  month  nbre_articles  cost  money  increase  market  \
0 1919-01-01  1919      1         228632  8523   9151      6747    5859   
1 1919-02-01  1919      2         195555  7521   8202      5128    4970   

   prices  wages  economy  decrease  currency  cost of living  recession  \
0    5359   2040      531       921       292             396         49   
1    4671   1946      468       620       270             339         59   

   purchasing power  cpi  price level  interest rates  market prices  \
0                54  138           50              36             79   
1                43   94           45              31             71   

   inflation  cost_rat  money_rat  increase_rat  market_rat  prices_rat  \
0          3  3.727825   4.002502       2.95103    2.562633    2.343941   
1          0  3.845977   4.194216       2.62228    2.541484    2.388586   

   wages_rat  economy_rat  decrease_rat  currency_rat  cost of living_rat  \
0   0.892264     0.232251      0.402831      0.127716            0.173204   
1   0.995116     0.239319      0.317046      0.138069            0.173353   

   recession_rat  purchasing power_rat   cpi_rat  price level_rat  \
0       0.021432              0.023619  0.060359         0.021869   
1       0.030171              0.021989  0.048068         0.023011   

   interest rates_rat  market prices_rat  inflation_rat  
0            0.015746           0.034553       0.001312  
1            0.015852           0.036307       0.000000

In [276]:
# Listes utiles (3): 
# Pourcentage des différents termes du champ lexical de l'inflation
selected_rat=[col for col in freq_sub.columns if col not in sub]


In [277]:
stacked_bar(
    freq_sub,
    'date',
    selected_rat,
    "Figure 5: Pourcentage d'articles par mois contenant les termes liés à l'inflation de 1919 à 1962",
    "Date",
    "Articles (%)",
    "Mot"
)

On peut tout d'abord s'intéresser au niveau agrégé. On constate un pic d'articles mentionnant des termes liés à l'inflation autour de 1920, ce qui correspond à une première période de forte inflation puis autour de 1933, avec plus de 20% d'articles pertinents. Cela coïncide avec la crise économique des années 30, période de forte déflation. La proportion d'article traitant de ces sujets baisse ensuite, notamment pendant la guerre. On peut envisager que d'autres sujets étaient alors jugés plus importants, même si cela semble rester un sujet, les pourcentages étant toujours relativement importants. On constate un deuxième pic, de même niveau que celui des années 30, à la fin des années 40, là encore période de forte inflation. La proportion diminue encore notamment à la fin des années 50. Cela pourrait correspondre à la stabilisation de l'inflation mais comme mentionné ci-dessus, moins d'articles sont disponibles sur cette période donc cela pourrait également jouer. Si on regarde de plus plus en détail, les proportions de mots mentionnés restent relativement stables.

<a id="introduction"></a>

### 2.3.3- Nombre d'occurences par an des termes les plus utilisés dans le champ lexical de l'inflation

Pour plus de lisibilité, on peut également s'intéresser aux fréquences par année et non plus par mois. 

In [278]:
# Création d'une table annuelle: on somme les variables numériques par année

freq_an = freq_sub.groupby(['year'])[num].sum()

freq_an=freq_an.reset_index() # pour que year soit une colonne à part entière

freq_an.head(20)

year    cost   money  increase  market  prices  wages  economy  decrease  \
0   1919  112156  110525     79916   71010   71119  27435     6942      8720   
1   1920  115992  114241     89723   76197   76702  21382     8428     11692   
2   1921  120049  125306     75564   87726   73710  26157    10617     15230   
3   1922  114063  121121     76217   82217   68192  19838     9500     13211   
4   1923   40293   38537     27214   27922   24938   5621     2981      4231   
5   1924   37610   35878     24132   25554   21939   3613     2721      3846   
6   1925   29051   25256     18251   15927   14559   2966     2697      2662   
7   1926   27332   24438     16274   15079   13168   2539     2025      2370   
8   1927   23996   19936     12716   12857    9545   1540     1376      1903   
9   1928   21697   18167     12622   11811    8484   1610     1331      1759   
10  1929   16647   16335     10969   11264    6462   1544     1039      1396   
11  1930   17230   17390     11349   12681    8488   1340     1222      2135   
12  1931   17147   18599     12295   11870    9456   2129     1721      2545   
13  1932   28882   27850     16642   17492   13901   2753     5386      3830   
14  1933   29775   28858     18679   19055   17304   5123     5354      3392   
15  1934   28125   27342     18342   17653   13878   3924     2718      2731   
16  1935   25665   24510     16167   13657   12275   3000     2107      2344   
17  1936   24984   23518     16374   13836   11706   3060     2092      2232   
18  1937   26167   21141     17382   13604   12423   4576     2519      2127   
19  1938   25482   22922     15082   13641   11297   3485     2471      2489   

    currency  cost of living  recession  purchasing power   cpi  price level  \
0       3964           13109        829               738  1214          753   
1       5117           10390       1105               761  1353          567   
2       5807            3697       1309              1089  1453          728   
3       6460            2717       1132              1101  1280          682   
4       2091             724        465               445   247          260   
5       1530             528        542               342   281          217   
6       1004             333        227               213   251          164   
7        939             227        320               203   328          155   
8        605             175        247               143   171          129   
9        630             107        210               190   226          127   
10       564             100        234                87   178           91   
11       460             129        393               186   187          199   
12       735             147        326               299    95          268   
13      2186             180        372               563   116          380   
14      4888             412        463              1337   136          804   
15      2642             331        437               694   144          387   
16      1940             258        376               425   118          230   
17      1760             260        314               401   118          176   
18      1172             353        967               405   126          191   
19      1239             192       1681               458   103          173   

    interest rates  market prices  inflation  nbre_articles  
0              308           1107         30        2762148  
1              684           1185         63        2785790  
2              650            940         70        3006578  
3              647            656         66        3024703  
4              157            213         26        1024242  
5              182            114         20         942234  
6              126             90         11         732926  
7               81            144          6         697498  
8               97            139          3         574284  
9               82    

In [279]:
# Graphique des fréquences annuelles

stacked_bar(
    freq_an,
    'year',
    selected,
    "Figure 6: Nombre d'occurences par an des termes liés à l'inflation de 1919 à 1962",
    "Année",
    "Nb occurences",
    "Mot"
)

<a id="introduction"></a>

### 2.3.4- Pourcentage d'articles par an contenant les termes les plus utilisés dans le champ lexical de l'inflation

In [280]:
# Création des pourcentages
for col in selected:
    freq_an.loc[:,f"{col}_rat"]=(freq_an.loc[:,f"{col}"]/freq_an.loc[:,'nbre_articles'])*100

freq_an.head(2)

year    cost   money  increase  market  prices  wages  economy  decrease  \
0  1919  112156  110525     79916   71010   71119  27435     6942      8720   
1  1920  115992  114241     89723   76197   76702  21382     8428     11692   

   currency  cost of living  recession  purchasing power   cpi  price level  \
0      3964           13109        829               738  1214          753   
1      5117           10390       1105               761  1353          567   

   interest rates  market prices  inflation  nbre_articles  cost_rat  \
0             308           1107         30        2762148  4.060463   
1             684           1185         63        2785790  4.163702   

   money_rat  increase_rat  market_rat  prices_rat  wages_rat  economy_rat  \
0   4.001415      2.893256    2.570825    2.574772   0.993249     0.251326   
1   4.100848      3.220738    2.735203    2.753330   0.767538     0.302535   

   decrease_rat  currency_rat  cost of living_rat  recession_rat  \
0      0.315696      0.143511            0.474594       0.030013   
1      0.419701      0.183682            0.372964       0.039666   

   purchasing power_rat   cpi_rat  price level_rat  interest rates_rat  \
0              0.026718  0.043951         0.027261            0.011151   
1              0.027317  0.048568         0.020353            0.024553   

   market prices_rat  inflation_rat  
0           0.040078       0.001086  
1           0.042537       0.002261

In [281]:
# Graphique des pourcentages d'apparition annuels
stacked_bar(
    freq_an,
    'year',
    selected_rat,
    "Figure 7: Pourcentage d'articles par an contenant les termes liés à l'inflation de 1919 à 1962",
    "Année",
    "Articles (%)",
    "Mot"
)

On constate ici aussi clairement deux pics, en 1933 et en 1947. La proportion des différents termes reste relativement constante.

<a id="introduction"></a>

# 3- Comparaisons de l'inflation mesurée et des statistiques de fréquences des termes lexicaux liés à l'inflation

<a id="introduction"></a>

## 3.1- Analyse agrégée

<a id="introduction"></a>

### 3.1.1- Analyse des associations statistiques entre l'inflation annuelle et le pourcentage total d'articles mentionnant des termes liés à l'inflation

#### Création du pourcentage total d'articles mentionnant les termes du champ lexical de l'inflation

In [282]:
# Analyse agrégée: (somme du nombre d'occurence pour chaque terme/ nbre d'articles)*100
freq_sub.loc[:,'total_rat'] = (freq_sub.loc[:,selected].sum(axis=1)/freq_sub.loc[:,"nbre_articles"])*100
freq_sub.head(1)

C:\Users\lisem\AppData\Local\Temp\ipykernel_28808\2863142479.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



date  year  month  nbre_articles  cost  money  increase  market  \
0 1919-01-01  1919      1         228632  8523   9151      6747    5859   

   prices  wages  economy  decrease  currency  cost of living  recession  \
0    5359   2040      531       921       292             396         49   

   purchasing power  cpi  price level  interest rates  market prices  \
0                54  138           50              36             79   

   inflation  cost_rat  money_rat  increase_rat  market_rat  prices_rat  \
0          3  3.727825   4.002502       2.95103    2.562633    2.343941   

   wages_rat  economy_rat  decrease_rat  currency_rat  cost of living_rat  \
0   0.892264     0.232251      0.402831      0.127716            0.173204   

   recession_rat  purchasing power_rat   cpi_rat  price level_rat  \
0       0.021432              0.023619  0.060359         0.021869   

   interest rates_rat  market prices_rat  inflation_rat  total_rat  
0            0.015746           0.034553       0.001312  17.595087

#### Figure 8: Comparaison du pourcentage d'inflation annuelle (en valeur absolue) et du pourcentage d'articles contenant des termes liés à l'inflation

In [283]:
def two_graphs(df1_x,df1_y,df2_x,df2_y,df1_name,df2_name, abs_name, titre):
    """
    Fonction traçant deux courbes sur un même graphique
    pour comparer les évolutions.
    ==================================================
    Paramètres:
    ==================================================
    df1_x: abscisse de la première courbe
    df1_y: ordonnée de la première courbe
    df2_x: abscisse de la deuxième courbe
    df2_y: ordonnée de la deuxième courbe
    df1_name: nom de la première courbe
    df2_name: nom de la deuxième courbe
    abs_name: nom de l'axe des abcisses
    titre: titre du graphique
    """

    graph = go.Figure()

    graph.add_trace(go.Scatter(
        x=df1_x, 
        y=df1_y, 
        mode='lines', 
        name=df1_name,
        yaxis='y' 
    ))

    graph.add_trace(go.Scatter(
        x=df2_x, 
        y=df2_y, 
        mode='lines', 
        name=df2_name,
        yaxis='y2'  
    ))

    graph.update_layout(
        title=titre,
        xaxis=dict(title=abs_name),
        yaxis=dict(title=df1_name, side='left'),
        yaxis2=dict(
            title=df2_name,
            side='right',
            overlaying='y'  
        ),
        template="plotly_dark"
)


    graph.show(config={"scrollZoom": True, "displayModeBar": True})

In [284]:
# Création d'un dataframe réduit à la période 1919-1962
CPI_40=CPI_sub[CPI_sub['year']>1918] 

two_graphs(
    CPI_40['date'],
    abs(CPI_40['inf_an']),
    freq_sub['date'],
    freq_sub['total_rat'],
    'Inflation (%, val abs.)',
    "Articles (%)", 
    "Date", 
    "Figure 8: Comparaison du pourcentage d'inflation annuelle (en valeur absolue) et du pourcentage d'articles contenant des termes liés à l'inflation de 1919 à 1962"
    )

On a choisi de comparer le pourcentage d'articles mentionnant des termes liés à l'inflation avec la valeur absolue de l'inflation pour prendre en compte de la seul ampleur des évolutions de prix et donc potentiellement du traitement de la thématique, sans tenir compte de leur direction.

De prime abord, il semble y avoir une liaison statistique entre les deux variables, ce que nous testons dans les sections suivantes. 

#### Tests de corrélation entre la valeur absolue de l'inflation annuelle et le pourcentage d'articles mentionnant des termes liés

Le choix a été fait de réaliser différents tests de corrélation entre l'inflation et le pourcentage d'articles mentionnant des termes liés. Nous gardons une mesure mensuelle pour conserver un maximum d'information et ,nous prenons des pourcentages afin de ne pas biaiser les tests par un nombre d'articles différent.
- test de corrélation paramétrique: Pearson, test de corrélation linéaire. 
$$
    Corr(X,Y)=\frac{Cov(X,Y)}{\sqrt{Var(X)*Var(Y)}}
$$
- tests de corrélation non paramétrique (basés sur le rang): 

-> tau de Kendall  
$$
    \tau = \frac{C - D}{\frac{1}{2}n(n-1)}
$$
avec C le nombre de paires concordantes (qui conservent le rang), D le nombre de paires discordantes et n le nombre d'observations. 

-> rho de Spearman
$$
    \rho = 1 - \frac{6 \sum d_i^2}{n(n^2 - 1)}
$$
avec *d* la différence de rang pour chaque observation et n le nombre total d'observations

Ces tests posent l'hypothèse nulle que les deux variables sont indépendantes. On pose un seuil de significativité à 5%.


In [285]:
# Fusion des tables de fréquence et de pourcentage d'inflation CHANGER CPI_40
inf_freq=pd.merge(CPI_40, freq_sub, on=['date', 'year', 'month'])

inf_freq.head()


date  value  year  month     inf_an  inf_neg  acceleration_12  \
0 1919-01-01   16.5  1919      1  17.857143        0              NaN   
1 1919-02-01   16.2  1919      2  14.893617        0              NaN   
2 1919-03-01   16.4  1919      3  17.142857        0              NaN   
3 1919-04-01   16.7  1919      4  17.605634        0              NaN   
4 1919-05-01   16.9  1919      5  16.551724        0              NaN   

   nbre_articles  cost  money  increase  market  prices  wages  economy  \
0         228632  8523   9151      6747    5859    5359   2040      531   
1         195555  7521   8202      5128    4970    4671   1946      468   
2         234087  8410   9873      5867    5786    5284   1969      522   
3         245278  8771   9725      6198    6031    5773   2016      527   
4         243206  8401   9259      5621    5768    5014   1567      506   

   decrease  currency  cost of living  recession  purchasing power  cpi  \
0       921       292             396         49                54  138   
1       620       270             339         59                43   94   
2       704       408             362         77                48  120   
3       689       301             267        127                55  100   
4       598       269             275         80                54   90   

   price level  interest rates  market prices  inflation  cost_rat  money_rat  \
0           50              36             79          3  3.727825   4.002502   
1           45              31             71          0  3.845977   4.194216   
2           60              47             83          3  3.592681   4.217663   
3           77              39            119          1  3.575942   3.964889   
4           61              22             55          3  3.454273   3.807061   

   increase_rat  market_rat  prices_rat  wages_rat  economy_rat  decrease_rat  \
0      2.951030    2.562633    2.343941   0.892264     0.232251      0.402831   
1      2.622280    2.541484    2.388586   0.995116     0.239319      0.317046   
2      2.506333    2.471731    2.257280   0.841140     0.222994      0.300743   
3      2.526929    2.458843    2.353656   0.821925     0.214858      0.280906   
4      2.311209    2.371652    2.061627   0.644310     0.208054      0.245882   

   currency_rat  cost of living_rat  recession_rat  purchasing power_rat  \
0      0.127716            0.173204       0.021432              0.023619   
1      0.138069            0.173353       0.030171              0.021989   
2      0.174294            0.154643       0.032894              0.020505   
3      0.122718            0.108856       0.051778              0.022424   
4      0.110606            0.113073       0.032894              0.022203   

    cpi_rat  price level_rat  interest rates_rat  market prices_rat  \
0  0.060359         0.021869            0.015746           0.034553   
1  0.048068         0.023011            0.015852           0.036307   
2  0.051263         0.025631            0.020078           0.035457   
3  0.040770         0.031393            0.015900           0.048516   
4  0.037006         0.025082            0.009046           0.022615   

   inflation_rat  total_rat  
0       0.001312  17.595087  
1       0.000000  17.630846  
2       0.001282  16.926613  
3       0.000408  16.640710  
4       0.001234  15.477825

In [286]:
def corr_tests(list1,list2):
    # Test de corrélation de Pearson
    print("TEST DE CORRELATION DE PEARSON:")
    r, p = pearsonr(list1, list2)
    print ("Le coefficient de corrélation de Pearson s'élève à ", r, " et sa p-value est de: ", p,".")
    if p<0.05:
        print("Le coefficient est donc significatif.")
        if r<0.30:
            print("Les variables sont de plus faiblement corrélées.")
        elif r>0.70:
            print("Les variables sont de plus fortement corrélées.")
        else: 
            print("Les variables sont de plus moyennement corrélées.")
    else:
        print("Le coefficient n'est donc pas significatif.")

    # Tau de Kendall
    print("TAU DE KENDALL:")
    tau,p=kendalltau(list1, list2)
    print("Le tau de Kendall s'élève à ", tau, " et sa p-value est de: ", p, ".")
    if p<0.05:
        print("Le coefficient est donc significatif.")
        if tau<0.30:
            print("Les variables sont de plus faiblement corrélées.")
        elif tau>0.70:
            print("Les variables sont de plus fortement corrélées.")
        else: 
            print("Les variables sont de plus moyennement corrélées.")
    else:
        print("Le coefficient n'est donc pas significatif.")

    # Rho de Spearman
    print("RHO DE SPEARMAN:")
    rho, p = spearmanr(list1, list2)
    print("Le coef de Spearman s'élève à ", rho, " avec une p-value de: ", p, ".") 
    if p<0.05:
        print("Le coefficient est donc significatif.")
        if rho<0.30:
            print("Les variables sont de plus faiblement corrélées.")
        elif rho>0.70:
            print("Les variables sont de plus fortement corrélées.")
        else: 
            print("Les variables sont de plus moyennement corrélées.")
    else:
        print("Le coefficient n'est donc pas significatif.")  

In [287]:
# Tests de corrélation entre la valeur absolue de l'inflation annuelle et le pourcentage d'apparition des termes du champ lexical de l'inflation
corr_tests(abs(inf_freq['inf_an']),inf_freq['total_rat'])

TEST DE CORRELATION DE PEARSON:
Le coefficient de corrélation de Pearson s'élève à  0.4866819819666136  et sa p-value est de:  9.47089004439658e-33 .
Le coefficient est donc significatif.
Les variables sont de plus moyennement corrélées.
TAU DE KENDALL:
Le tau de Kendall s'élève à  0.30373879616050026  et sa p-value est de:  2.0422559293838835e-25 .
Le coefficient est donc significatif.
Les variables sont de plus moyennement corrélées.
RHO DE SPEARMAN:
Le coef de Spearman s'élève à  0.44032510987275153  avec une p-value de:  1.8895282275455734e-26 .
Le coefficient est donc significatif.
Les variables sont de plus moyennement corrélées.


<a id="introduction"></a>

#### 3.1.2- Analyse via les moyennes mobiles (ma)

#### Moyennes mobiles

L'utilisation de moyennes mobiles vise à supprimer les fluctuations transitoires pour mettre en valeur les tendances de long terme. On choisit ici une fenêtre d'un an. On remplace donc chaque valeur par la moyenne des douze valeurs précédentes.

In [288]:
# Moyennes mobiles de l'inflation annuelle et du pourcentage d'articles mentionnant des termes liés avec une fenêtre d'un an
inf_freq['inf_ma'] = inf_freq['inf_an'].rolling(window=12).mean()
inf_freq['tot_rat_ma'] = inf_freq['total_rat'].rolling(window=12).mean()

#### Figure 9: Comparaison des moyennes mobiles de l'inflation annuelle (en valeur absolue) et du pourcentage d'articles mentionnant des termes liés à l'inflation

In [289]:
# Visualisation après lissage via moyennes mobiles
two_graphs(
    inf_freq['date'],
    abs(inf_freq['inf_ma']),
    inf_freq['date'],
    inf_freq['tot_rat_ma'],
    'Inflation ma (%, val abs.)',
    "Articles ma (%)", 
    "Date", 
    "Figure 9: Comparaison des moyennes mobiles de l'inflation annuelle (en valeur absolue) et du pourcentage d'articles mentionnant des termes liés à l'inflation de 1919 à 1962"
    )

#### Tests de corrélation entre la valeur absolue de l'inflation annuelle et le pourcentage d'articles mentionnant des termes liés (en moyennes mobiles sur 12 mois)

In [290]:
# Corrélations entre variables lissées
inf_freq_cleaned = inf_freq.replace([np.inf, -np.inf], np.nan).dropna(subset=['inf_ma', 'tot_rat_ma'])
corr_tests(abs(inf_freq_cleaned['inf_ma']),inf_freq_cleaned['tot_rat_ma'])

TEST DE CORRELATION DE PEARSON:
Le coefficient de corrélation de Pearson s'élève à  0.5799006266790503  et sa p-value est de:  8.732616130985067e-48 .
Le coefficient est donc significatif.
Les variables sont de plus moyennement corrélées.
TAU DE KENDALL:
Le tau de Kendall s'élève à  0.31437053923044567  et sa p-value est de:  1.1871761921873666e-26 .
Le coefficient est donc significatif.
Les variables sont de plus moyennement corrélées.
RHO DE SPEARMAN:
Le coef de Spearman s'élève à  0.45038382200824373  avec une p-value de:  3.4370349546672015e-27 .
Le coefficient est donc significatif.
Les variables sont de plus moyennement corrélées.


On retrouve les mêmes ordres de grandeur que dans les tests précédents, avec des variables positivement moyennement corrélées. 

<a id="introduction"></a>

### 3.1.3- Comparaison via les quartiles

On va maintenant classer chaque mois selon les quartiles d'inflation et de fréquence pour comparer les deux variables.

In [291]:
def quart(name,var): 
    """
    Fonction classant les observations en quatre catégories basés sur les quartiles d'une variable.
    ==============================================================================================
    Paramètres
    ==============================================================================================
    name: nom de la variable catégorielle prenant les valeurs 1,2,3 et 4: par ex "inf_qu"
    var: série dont sont calculés les quartiles: par ex: inf_freq["inf_an"]
    """
    inf_freq.loc[:,name]=0

    q1=var.quantile(0.25)
    q2=var.quantile(0.50)
    q3=var.quantile(0.75)
    
    inf_freq.loc[
        var<q1, 
        name
        ] = 1
    inf_freq.loc[
        (var>=q1) & (var<q2), 
        name
        ] = 2
    inf_freq.loc[
        (var>=q2) & (var<q3), 
        name
        ] = 3
    inf_freq.loc[
        var>=q3, 
        name
        ] = 4

In [292]:
# Classement des dates en quatre catégories selon les quartiles des pourcentages du nombre total d'articles 
quart('tot_rat_qu',inf_freq['total_rat'])


In [293]:
# Classement des dates en quatre catégories selon les quartiles des pourcentages d'inflation annuelle
quart('inf_qu', abs(inf_freq['inf_an']))

In [294]:
# fonction créant le dataframe 
def quart_df(list_rows, list_col, nb_rows, nb_col, quart_row, quart_col, df):
    """
    Fonction qui crée un tableau croisé comptant les occurences appartenant à chaque catégorie.
    list_rows: liste d'en-têtes des lignes (modalités var 1)
    list_col: liste d'en-têtes des colonnes (modalités var 2)
    nb_rows: nb de lignes 
    nb_col: nb de colonnes 
    quart_row: nom de la colonne var 1: par ex inf_freq['inf_qu']
    quart_col: nom de la colonne var 2: par ex inf_freq['tot_rat_qu']
    df: nom du dataframe

    """
    quartiles=pd.DataFrame(columns=list_col, index=list_rows)
    for i in range(nb_rows):
        for j in range(nb_col):
            count=df[(quart_row==i+1) & (quart_col==j+1)].shape[0]
            quartiles.iloc[i,j]=count
    return quartiles



In [295]:
freq = ['Freq: quartile 1', 'Freq: quartile 2', 'Freq: quartile 3', 'Freq: quartile 4']
inf = ['Inflation: quartile 1', 'Inflation: quartile 2', 'Inflation: quartile 3', 'Inflation: quartile 4']
quartiles=quart_df(inf, freq, 4, 4, inf_freq['inf_qu'], inf_freq['tot_rat_qu'], inf_freq)

#### Figure 10: Heatmap comparant les quartiles d'inflation et de fréquence

In [296]:
def heatmap(df, x_title, y_title, col_title, titre):
    """
    df: dataframe
    x_title: titre abcisses
    y_title: titre ordonnées
    col_title: label du contenu des cases
    titre: titre du graphique
    """
    graph = px.imshow(
        df,
        text_auto=True,
        labels=dict(x=x_title, y=y_title, color=col_title),
        title=titre
        )

    graph.update_layout(template="plotly_dark")

    graph.show(config={"scrollZoom": True, "displayModeBar": True})

In [297]:
heatmap(
    quartiles,
    "Articles",
    "Inflation",
    "Nb observations",
    "Figure 10: Croisement des quartiles d'inflation (en valeur absolue) et des quartiles de fréquence"
)

On a donc 77 observations qui ont un pourcentage d'inflation dans le dernier quartile et un pourcentage d'articles mentionnant des termes liés à l'inflation dans le dernier quartile. C'est l'effectif le plus élevé sur le tableau. On constate bien des effectifs assez élevés sur la diagonale et plus faibles dans les coins opposés ce qui va bien dans le sens d'une corrélation positives entre les deux variables. On va le confirmer avec un test d'indépendance du $\chi^{2}$.

#### Test d'indépendance du $\chi^{2}$


$$
    \chi^2 = \sum \frac{(O_i - E_i)^2}{E_i}
$$


où les $O_i$ sont les fréquences observées et $E_i$ les fréquences attendues (sous l'hypothèse nulle d'indépendance).

On rejette l'hypothèse nulle si la statistique du $\chi^2$ est supérieure à une valeur critique qui dépend des degrés de liberté et d'un seuil qu'on fixe à 0.05.

In [298]:
def chi_test(df,):
    """
    Fonction réalisant un test du chi2 avec un seuil de significativité à 5%.
    ============================================================================
    Paramètres:
    ============================================================================
    df: tableau à double entrée

    """
    for col in df.columns:
        col = pd.to_numeric(col, errors='coerce')
    array=df.to_numpy().tolist()
    stat, p, dof, expected =chi2_contingency(array)
    print("Statistique du chi2:", stat)
    print("P-value:", p)
    print("Degrés de liberté:", dof)
    print("Fréquences attendues:\n", expected)
    critical_value = chi2.ppf(1 - 0.05, dof)
    if p<0.05 and stat>critical_value:
        print("Les deux variables sont bien associées.")
        
    

In [299]:
chi_test(quartiles)

Statistique du chi2: 127.53320482175444
P-value: 3.8111923132727536e-23
Degrés de liberté: 9
Fréquences attendues:
 [[32.75 32.75 32.75 32.75]
 [32.5  32.5  32.5  32.5 ]
 [33.75 33.75 33.75 33.75]
 [33.   33.   33.   33.  ]]
Les deux variables sont bien associées.


<a id="introduction"></a>

## 3.2- Prolongements de l'analyse 

<a id="introduction"></a>

### 3.2.1- Analyse du lien entre accélération de l'inflation et traitement médiatique

#### Figure 11: Comparaison de l'accélération (en valeur absolue) et du pourcentage d'articles mentionnant des termes liés à l'inflation de 1919 à 1962

In [300]:
two_graphs(
    CPI_40['date'],
    abs(CPI_40['acceleration_12']),
    freq_sub['date'],
    freq_sub['total_rat'],
    'Accélération (%, val abs.)',
    "Articles (%)", 
    "Date", 
    "Figure 11: Comparaison de l'accélération (en valeur absolue) et du pourcentage d'articles mentionnant des termes liés à l'inflation de 1919 à 1962"
    )

Il semblerait que la corrélation soit moins forte entre ces deux variables.

#### Tests de corrélation entre la valeur absolue du pourcentage d'accélération de l'inflation et le pourcentage d'articles mentionnant des termes liés à l'inflation

In [301]:
# Nouvelle corrélation:
inf_freq_cleaned = inf_freq.replace([np.inf, -np.inf], np.nan).dropna(subset=['acceleration_12', 'total_rat'])
corr_tests(abs(inf_freq_cleaned['acceleration_12']),inf_freq_cleaned['total_rat'])


TEST DE CORRELATION DE PEARSON:


Le coefficient de corrélation de Pearson s'élève à  -0.04034031357360278  et sa p-value est de:  0.36280008157721877 .
Le coefficient n'est donc pas significatif.
TAU DE KENDALL:
Le tau de Kendall s'élève à  -0.009745947653965172  et sa p-value est de:  0.7420807675203762 .
Le coefficient n'est donc pas significatif.
RHO DE SPEARMAN:
Le coef de Spearman s'élève à  -0.013870905007774123  avec une p-value de:  0.7544301354802844 .
Le coefficient n'est donc pas significatif.


Aucun des tests n'est significatif. On ne peut donc pas conclure à une association entre ces deux variables.

<a id="introduction"></a>

### 3.2.2- Analyse par terme 

Au delà de l'analyse des fréquences de l'ensemble du champ lexical, on peut s'intéresser à des termes en particulier, notamment ceux qu'on a relevés comme les plus fréquents.

#### Cost

In [302]:
two_graphs(
    CPI_40['date'],
    abs(CPI_40['inf_an']),
    freq_sub['date'],
    freq_sub['cost_rat'],
    'Inflation (%, val abs.)',
    "Cost (%)", 
    "Date", 
    "Figure 12: Comparaison du pourcentage d'inflation annuelle (en valeur absolue) et du pourcentage d'apparition de cost"
    )

In [303]:
corr_tests(abs(inf_freq['inf_an']),inf_freq['cost_rat'])

TEST DE CORRELATION DE PEARSON:
Le coefficient de corrélation de Pearson s'élève à  0.05515900900891407  et sa p-value est de:  0.20572182391271085 .
Le coefficient n'est donc pas significatif.
TAU DE KENDALL:
Le tau de Kendall s'élève à  0.009747400692105548  et sa p-value est de:  0.7381207492506627 .
Le coefficient n'est donc pas significatif.
RHO DE SPEARMAN:
Le coef de Spearman s'élève à  0.016525657176599973  avec une p-value de:  0.7047943544596417 .
Le coefficient n'est donc pas significatif.


Deux tests sur trois sont non significatifs, on ne peut donc pas conclure à une association des deux variables. On peut néanmoins tenter de les lisser.

In [304]:
# en ma
inf_freq['cost_rat_ma'] = inf_freq['cost_rat'].rolling(window=12).mean()
inf_freq_cleaned = inf_freq.replace([np.inf, -np.inf], np.nan).dropna(subset=['inf_ma', 'cost_rat_ma'])
corr_tests(abs(inf_freq_cleaned['inf_ma']),inf_freq_cleaned['cost_rat_ma'])


TEST DE CORRELATION DE PEARSON:
Le coefficient de corrélation de Pearson s'élève à  0.08515923631132237  et sa p-value est de:  0.05297198982273567 .
Le coefficient n'est donc pas significatif.
TAU DE KENDALL:
Le tau de Kendall s'élève à  0.016628681103050855  et sa p-value est de:  0.5719219721643543 .
Le coefficient n'est donc pas significatif.
RHO DE SPEARMAN:
Le coef de Spearman s'élève à  0.01564773976091299  avec une p-value de:  0.7226247119027144 .
Le coefficient n'est donc pas significatif.


Après le lissage, les tests ne sont toujours pas significatifs. On ne peut donc pas conclure à une association de ces variables.

#### Money

In [305]:
two_graphs(
    CPI_40['date'],
    abs(CPI_40['inf_an']),
    freq_sub['date'],
    freq_sub['money_rat'],
    'Inflation (%, val abs.)',
    "Money (%)", 
    "Date", 
    "Figure 13: Comparaison du pourcentage d'inflation annuelle (en valeur absolue) et du pourcentage d'apparition de money"
    )

Au vu de la forte volatilité, on vérifie tout en suite en moyennes mobiles.

In [306]:
# en ma
inf_freq['money_rat_ma'] = inf_freq['money_rat'].rolling(window=12).mean()
inf_freq_cleaned = inf_freq.replace([np.inf, -np.inf], np.nan).dropna(subset=['inf_ma', 'money_rat_ma'])
corr_tests(abs(inf_freq_cleaned['inf_ma']),inf_freq_cleaned['money_rat_ma'])

TEST DE CORRELATION DE PEARSON:
Le coefficient de corrélation de Pearson s'élève à  0.28416620489739497  et sa p-value est de:  4.6480920587832805e-11 .
Le coefficient est donc significatif.
Les variables sont de plus faiblement corrélées.
TAU DE KENDALL:
Le tau de Kendall s'élève à  0.10146644276316064  et sa p-value est de:  0.0005628090323452894 .
Le coefficient est donc significatif.
Les variables sont de plus faiblement corrélées.
RHO DE SPEARMAN:
Le coef de Spearman s'élève à  0.17430260762157676  avec une p-value de:  6.771504844560133e-05 .
Le coefficient est donc significatif.
Les variables sont de plus faiblement corrélées.


On conclut donc à une association faible. 

#### Inflation
Malgré le nombre d'occurences limité du terme, on regarde tout de même le lien entre l'apparition du terme inflation et le pourcentage d'inflation.

In [307]:
two_graphs(
    CPI_40['date'],
    abs(CPI_40['inf_an']),
    freq_sub['date'],
    freq_sub['inflation_rat'],
    'Inflation (%, val abs.)',
    "Article (%)", 
    "Date", 
    "Figure 14: Comparaison du pourcentage d'inflation annuelle (en valeur absolue) et du pourcentage d'apparition de inflation"
    )

In [308]:
corr_tests(abs(inf_freq['inf_an']),inf_freq['inflation_rat'])

TEST DE CORRELATION DE PEARSON:
Le coefficient de corrélation de Pearson s'élève à  0.11567548594338556  et sa p-value est de:  0.00779882147666649 .
Le coefficient est donc significatif.
Les variables sont de plus faiblement corrélées.
TAU DE KENDALL:
Le tau de Kendall s'élève à  0.12764154881331097  et sa p-value est de:  1.4785673530580187e-05 .
Le coefficient est donc significatif.
Les variables sont de plus faiblement corrélées.
RHO DE SPEARMAN:
Le coef de Spearman s'élève à  0.1823687904138809  avec une p-value de:  2.486844523339911e-05 .
Le coefficient est donc significatif.
Les variables sont de plus faiblement corrélées.


In [309]:
inf_freq['inf_rat_ma'] = inf_freq['inflation_rat'].rolling(window=12).mean()
inf_freq_cleaned = inf_freq.replace([np.inf, -np.inf], np.nan).dropna(subset=['inf_ma', 'inf_rat_ma'])
corr_tests(abs(inf_freq_cleaned['inf_ma']),inf_freq_cleaned['inf_rat_ma'])

TEST DE CORRELATION DE PEARSON:
Le coefficient de corrélation de Pearson s'élève à  0.2691261659534616  et sa p-value est de:  4.984404098053379e-10 .
Le coefficient est donc significatif.
Les variables sont de plus faiblement corrélées.
TAU DE KENDALL:
Le tau de Kendall s'élève à  0.22565272479079237  et sa p-value est de:  1.7469243370561473e-14 .
Le coefficient est donc significatif.
Les variables sont de plus faiblement corrélées.
RHO DE SPEARMAN:
Le coef de Spearman s'élève à  0.30207637335849175  avec une p-value de:  2.275795483605e-12 .
Le coefficient est donc significatif.
Les variables sont de plus moyennement corrélées.


On peut en conclure à une corrélation moyenne entre la présence du terme inflation et le pourcentage d'inflation ce qui semble rassurant.

<a id="introduction"></a>

# 4- Modélisation

<a id="introduction"></a>

## 4.1- Régression linéaire

Une première façon de modéliser le lien entre inflation et traitement médiatique de cette thématique peut consister en une régression linéaire. Les perceptions d'inflation évaluées à travers le traitement médiatique de ce sujet peuvent constituer un indicateur d'inflation et être utilisées pour du *nowcasting* de l'inflation par exemple. On cherche donc alors à voir le pourcentage d'apparition des termes liés à l'inflation donne une prédiction satisfaisante du pourcentage d'inflation. Mais on peut également envisager une relation inverse. En effet, les perceptions d'inflation sont un objet d'étude à part entière en économie en raison de leurs multiples enjeux. On peut par exemple citer les nombreux travaux sur l'impact des annonces des banques centrales sur les anticipations d'inflation. Dès lors, si on prend les perceptions mesurées par le traitement médiatique comme variable d'intérêt, on peut chercher à évaluer à quel point l'inflation mesurée permet de les prédire. On s'abstiendra en revanche de toute analyse causale. 

In [310]:
def lin_reg(cov,dep):
    """
    Fonction réalisant une régression linéaire simple robuste à l'homoscédasticité.
    ===============================================================================
    Paramètres
    ===============================================================================
    cov: covariable
    dep: variable dépendante
    """
    x=cov 
    y=dep 

    x = sm.add_constant(x) #constante


    model = sm.OLS(y, x)
    results = model.fit(cov_type='HC3')
    print(results.summary())




<a id="introduction"></a>

### 3.1.1- Le traitement médiatique de l'inflation comme indicateur de l'inflation?

In [311]:
#Pourcentage d'inflation sur fréquences
lin_reg(inf_freq["total_rat"],abs(inf_freq["inf_an"]))

                            OLS Regression Results                            
Dep. Variable:                 inf_an   R-squared:                       0.237
Model:                            OLS   Adj. R-squared:                  0.235
Method:                 Least Squares   F-statistic:                     99.00
Date:                Sat, 28 Dec 2024   Prob (F-statistic):           1.74e-21
Time:                        15:20:13   Log-Likelihood:                -1489.0
No. Observations:                 528   AIC:                             2982.
Df Residuals:                     526   BIC:                             2990.
Df Model:                           1                                         
Covariance Type:                  HC3                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
const        -12.2262      1.562     -7.827      0.0

Le coefficient associé au pourcentage d'article mentionnant des termes liés à l'inflation est positif. Il s'élève de plus à 1,0 ce qui signifie qu'une augmentation de 1 point du pourcentage d'article est associée à une augmentation de 1 point du pourcentage d'inflation en valeur absolue. La p value est nulle donc ce coefficient est significatif. La variance du pourcentage d'article permet d'expliquer 24% de la variance de l'inflation. 

In [312]:
# En ma
lin_reg(inf_freq.loc[inf_freq["year"] > 1919, "tot_rat_ma"],abs(inf_freq.loc[inf_freq["year"] > 1919, "inf_ma"]))

                            OLS Regression Results                            
Dep. Variable:                 inf_ma   R-squared:                       0.334
Model:                            OLS   Adj. R-squared:                  0.333
Method:                 Least Squares   F-statistic:                     127.6
Date:                Sat, 28 Dec 2024   Prob (F-statistic):           1.39e-26
Time:                        15:20:13   Log-Likelihood:                -1354.7
No. Observations:                 516   AIC:                             2713.
Df Residuals:                     514   BIC:                             2722.
Df Model:                           1                                         
Covariance Type:                  HC3                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
const        -16.2216      1.702     -9.531      0.0

Le coefficient associé au pourcentage d'article mentionnant des termes liés à l'inflation en moyenne mobile est positif. Il s'élève de plus à 1.3 ce qui signifie qu'une augmentation de 1 point du pourcentage d'articles est associé à une augmentation de 1.3 point du pourcentage d'inflation en moyenne mobile en valeur absolue. La p value est nulle donc ce coefficient est significatif. 

La variance du pourcentage d'articles permet en outre d'expliquer 33% de la variance d'inflation.

**Conclusion partielle**: Le pourcentage d'articles mentionnant des termes du champ lexical de l'inflation semble donc être une covariable utile pour prédire le pourcentage d'inflation. Il faut bien sûr envisager de la compléter par d'autres variables, ce qu'on pourrait faire en prolongement de notre sujet. On peut penser à d'autres mesures des perceptions, disponibles en temps réel si le but est le *nowcasting*, par exemple une analyse via les réseaux sociaux. Il faut aussi prendre en compte des facteurs plus causaux comme d'autres variables économiques, par exemple la croissance et le chômage.

<a id="introduction"></a>

### 3.1.2- L'inflation mesurée comme indicateur de l'inflation perçue dans les journaux

In [313]:
# Fréquences sur pourcentage d'Inflation
lin_reg(abs(inf_freq["inf_an"]),inf_freq["total_rat"])



                            OLS Regression Results                            
Dep. Variable:              total_rat   R-squared:                       0.237
Model:                            OLS   Adj. R-squared:                  0.235
Method:                 Least Squares   F-statistic:                     163.4
Date:                Sat, 28 Dec 2024   Prob (F-statistic):           8.82e-33
Time:                        15:20:13   Log-Likelihood:                -1090.2
No. Observations:                 528   AIC:                             2184.
Df Residuals:                     526   BIC:                             2193.
Df Model:                           1                                         
Covariance Type:                  HC3                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
const         14.9419      0.109    136.791      0.0

Le coefficient associé au pourcentage d'inflation en valeur absolue est positif. Il s'élève de plus à 0.23 ce qui signifie qu'une augmentation de 1 point du pourcentage d'inflation est associée à une augmentation de 0.23 point du pourcentage d'articles mentionnant des termes liés à l'inflation. La p value est nulle donc ce coefficient est significatif. 

La variance du pourcentage d'inflation permet en outre d'expliquer 24% de la variance du pourcentage d'articles.

In [314]:
lin_reg(abs(inf_freq.loc[inf_freq["year"] > 1919, "inf_ma"]),inf_freq.loc[inf_freq["year"] > 1919, "tot_rat_ma"])

                            OLS Regression Results                            
Dep. Variable:             tot_rat_ma   R-squared:                       0.334
Model:                            OLS   Adj. R-squared:                  0.333
Method:                 Least Squares   F-statistic:                     332.9
Date:                Sat, 28 Dec 2024   Prob (F-statistic):           1.02e-57
Time:                        15:20:17   Log-Likelihood:                -950.93
No. Observations:                 516   AIC:                             1906.
Df Residuals:                     514   BIC:                             1914.
Df Model:                           1                                         
Covariance Type:                  HC3                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
const         14.8883      0.085    174.690      0.0

Le coefficient associé au pourcentage d'inflation en valeur absolue et en moyenne mobile est positif. Il s'élève de plus à 0.26 ce qui signifie qu'une augmentation de 1 point du pourcentage d'inflation est associée à une augmentation de 0.26 point du pourcentage d'articles en moyenne mobile mentionnant des termes liés à l'inflation. La p value est nulle donc ce coefficient est significatif. 

La viarance du pourcentage d'inflation permet en outre d'expliquer 33% de la variance du pourcentage d'articles.

**Conclusion partielle**: le pourcentage d'inflation semble donc être une variable utile pour prédire les perceptions d'inflation. Il faut également envisager de la compléter par d'autres variables, même si les résultats seraient sûrement moins concluants que les précédents, dans la mesure on peut s'attendre à une prédictibilité moins forte des perceptions. Au-delà de chercher à prédire les perceptions d'inflation, on peut cependant déjà aller plus loin dans l'analyse en s'intéressant à la manière dont est perçue l'inflation grâce à un modèle d'analyse de sentiments.

<a id="introduction"></a>

## 3.2- Analyse de sentiments

Nettoyage du texte

In [9]:
#df=pd.read_parquet("ArticlesInflation/AllInflation.parquet")
with fs.open(f"{path}/AllInflation.parquet") as f:
    df = pd.read_parquet(f)

In [10]:
def clean_text(text):
    stop_words = set(stopwords.words("english"))
    text = text.lower()
    # Remove punctuation and stop words
    text = "".join([char for char in text if char not in string.punctuation])
    words = text.split()
    return " ".join([word for word in words if word not in stop_words])

def lemmatize_text(text):
    lemmatizer = nltk.WordNetLemmatizer()
    words = text.split()
    return " ".join([lemmatizer.lemmatize(word) for word in words])

def dereference_dico(dico):
    return dico["article"]

Ici la tokenization est implicite : les tokens sont chaque mot, cette approche peut être problématique si jamais les textes ont un format inhabituel comme des contractions ou des urls etc... Mais dans le cadre d'articles de presse, surtout d'anciens articles de presse il ne devrait y avoir aucun soucis

In [25]:
corpus=df["Article"]
corpus=corpus.apply(dereference_dico)
print(corpus.head())
corpus=corpus.apply(clean_text)
print(corpus.head())

0    BEST MAKES OF guaranteed tires at\n\n\nless th...
1    MAKE YOUR WALL PAPER clean and\n\n\nsweet agai...
2    STORIES. POEMS, PLAYS. ETC., are\n\n\nwanted f...
3    VV1ANTED-An experienced man on punch press and...
4    Have you lost a sum of money? Glasses. Pins an...
Name: Article, dtype: object
0    best makes guaranteed tires less dealers pay f...
1    make wall paper clean sweet simple formula suc...
2    stories poems plays etc wanted publication goo...
3    vv1antedan experienced man punch press eyelet ...
4    lost sum money glasses pins rings found surpri...
Name: Article, dtype: object


In [26]:
corpus=corpus.apply(lemmatize_text)
df["Treated"]=corpus

In [11]:
df["Article"]=df["Article"].apply(dereference_dico)
print(df.head())

                 Title     Date  \
0        The commoner.  1919-01   
1        The commoner.  1919-01   
2        The commoner.  1919-01   
3  New Britain herald.  1919-01   
4  New Britain herald.  1919-01   

                                             Article  
0  BEST MAKES OF guaranteed tires at\n\n\nless th...  
1  MAKE YOUR WALL PAPER clean and\n\n\nsweet agai...  
2  STORIES. POEMS, PLAYS. ETC., are\n\n\nwanted f...  
3  VV1ANTED-An experienced man on punch press and...  
4  Have you lost a sum of money? Glasses. Pins an...  


In [12]:
from sklearn.feature_extraction.text import TfidfVectorizer
vectorizer = TfidfVectorizer()

corpus=df["Treated"]
x = vectorizer.fit_transform(corpus)

In [16]:
print(type(x))
print(x.shape)

<class 'scipy.sparse._csr.csr_matrix'>
(3957020, 13988006)


In [33]:
toLabeled=df.sample(n=10000, random_state=42)
toLabeled=toLabeled[["Title","Date","Article"]]

In [34]:
print(toLabeled.head())

                        Title     Date  \
122716    New Britain herald.  1930-05   
557122      Norwich bulletin.  1920-07   
40954           Evening star.  1960-10   
73882   The Washington times.  1932-03   
131569          Evening star.  1952-10   

                                                  Article  
122716  New York, May ? [Pl-Curb prices huttered irreg...  
557122  number in town have received ti.e handsome. Da...  
40954   TRUSTEES SALE OF VALUABLE\nTWO-STORY BRICK DWE...  
73882   The market value of so repre-,\nsentative stoc...  
131569  the second floor there was displayed "a\ncoron...  


In [36]:
toLabeled.to_csv("ArticlesInflation/ToLabeled.csv")
toLabeledReduit=toLabeled.sample(n=100, random_state=42)
toLabeledReduit.to_csv("ArticlesInflation/ToLabeledReduit.csv")

Selection des articles parlant d'inflation à 100%

In [9]:
mots_inflation=["inflation", "disinflation", "inflationary", "deflation", "devaluation","recession","price level", "wage growth", "economic downturn", "monetary policy","inflation rate","interest rates", "price stability", "consumption basket", "purchasing power"]
articlesInflationSur=df[df["Article"].str.contains("|".join(mots_inflation), case=False)] # marche grâce aux regex
print(articlesInflationSur.head())

In [15]:
print(articlesInflationSur.shape)

(56337, 3)


In [20]:
toLabeled=articlesInflationSur.sample(n=100, random_state=42)
toLabeled.to_csv("ArticlesInflation/toLabelled.csv")

Utilisation de ChatGPT et vérifié à la main pour label les données

In [12]:
labeled=pd.read_csv("ArticlesInflation/ManuallyLabelledArticles.csv")
print(labeled.head())
print(labeled.shape)

   Unnamed: 0                     Title     Date  \
0       87446    Imperial Valley press.  1944-11   
1      133641  The Daily Alaska empire.  1935-09   
2       24042             Smyrna times.  1955-09   
3       37164             Evening star.  1934-06   
4       29819     The Washington times.  1934-05   

                                             Article     Label  
0  Here Gre 8 big reasons for buying tho\nsanst y...  Positive  
1  Designed to bring the farm program within the\...   Neutral  
2  A federal bearing to determine\nwhether the mi...   Neutral  
3  By the Associated Press.\n\n\nMembership in th...  Positive  
4  1--WE.\n\n\nThese three phases are not un-\nre...  Negative  
(100, 5)


In [42]:
print(labeled["Label"].value_counts())

Label
Neutral     38
Negative    35
Positive    27
Name: count, dtype: int64


In [43]:
texts=labeled["Article"]
labels=labeled["Label"]
texts=texts.apply(clean_text)
texts=texts.apply(lemmatize_text)

In [44]:
def numerical_label(label):
    if label=="Positive":
        return 0
    elif label=="Neutral":
        return 1
    else:
        return 2
labels=labels.apply(numerical_label)

In [46]:
print(labels.value_counts())
print(labels.isna().sum())

Label
1    38
2    35
0    27
Name: count, dtype: int64
0


In [47]:

vectorizer = TfidfVectorizer()
x=vectorizer.fit_transform(texts)

In [48]:
y=labels
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=42)

In [49]:
from sklearn.svm import SVC
svm_model = SVC()
svm_model.fit(x_train, y_train)

SVC()

In [53]:
from sklearn.metrics import accuracy_score, classification_report

# Predict on the test set
y_pred = svm_model.predict(x_test)
# Evaluate the performance
print("Accuracy:", accuracy_score(y_test, y_pred))
print("Classification Report:\n", classification_report(y_test, y_pred))


[1 1 1 1 1 1 1 1 1 1 1 1 2 1 1 1 1 1 1 1]
83    1
53    2
70    2
45    1
44    2
39    1
22    1
80    1
10    0
0     0
18    2
30    1
73    2
33    0
90    1
4     2
76    0
77    2
12    2
31    0
Name: Label, dtype: int64
Accuracy: 0.4
Classification Report:
               precision    recall  f1-score   support

           0       0.00      0.00      0.00         5
           1       0.37      1.00      0.54         7
           2       1.00      0.12      0.22         8

    accuracy                           0.40        20
   macro avg       0.46      0.38      0.25        20
weighted avg       0.53      0.40      0.28        20



c:\ProgramData\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\ProgramData\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\ProgramData\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


Comme on peut le voir, c'est NUL

Essayons maintenant d'utiliser ce modèle https://huggingface.co/cardiffnlp/twitter-roberta-base-sentiment?library=transformers

In [3]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification

c:\ProgramData\Python\Python312\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:
tokenizer = AutoTokenizer.from_pretrained("cardiffnlp/twitter-roberta-base-sentiment")
model = AutoModelForSequenceClassification.from_pretrained("cardiffnlp/twitter-roberta-base-sentiment")

Contrairement au modèle SVM il faut donner le texte brut aux modèles basé sur roBERTa

In [6]:
labelled=pd.read_csv("ArticlesInflation/ManuallyLabelledArticles.csv")
print(labelled.head())
print(labelled.shape)

   Unnamed: 0                     Title     Date  \
0       87446    Imperial Valley press.  1944-11   
1      133641  The Daily Alaska empire.  1935-09   
2       24042             Smyrna times.  1955-09   
3       37164             Evening star.  1934-06   
4       29819     The Washington times.  1934-05   

                                             Article     Label  
0  Here Gre 8 big reasons for buying tho\nsanst y...  Positive  
1  Designed to bring the farm program within the\...   Neutral  
2  A federal bearing to determine\nwhether the mi...   Neutral  
3  By the Associated Press.\n\n\nMembership in th...  Positive  
4  1--WE.\n\n\nThese three phases are not un-\nre...  Negative  
(100, 5)


On étiquette differement que précédement pour se conformer aux notations du modèles

Ensuite comme les articles peuvent être long nous activons le return_overflowing_tokens

In [7]:
labels=labelled["Label"]
texts=labelled["Article"]
def numerical_label_BERT(label):
    if label=="Positive":
        return 2
    elif label=="Neutral":
        return 1
    else:
        return 0
tokenNumber=512
labels=labels.apply(numerical_label_BERT)
texts=tokenizer(texts.tolist(),max_length=tokenNumber, truncation=True, padding=True,stride=128, return_overflowing_tokens=True, return_tensors="pt")
overflow_to_sample_mapping = texts['overflow_to_sample_mapping']
input_ids = texts['input_ids']
attention_mask = texts['attention_mask']
print(input_ids)
print(input_ids.shape)

tensor([[    0, 11773,  6879,  ...,     1,     1,     1],
        [    0, 28324,  9044,  ...,     8,    25,     2],
        [    0,  1717,  3894,  ...,     1,     1,     1],
        ...,
        [    0,     5,   220,  ...,     1,     1,     1],
        [    0, 25767, 20048,  ...,     1,     1,     1],
        [    0, 12778,   548,  ...,     1,     1,     1]])
torch.Size([147, 512])


Il faut ensuite relier les chunks aux articles c'est là qu'intervient overflow_to_sample_mapping

attention_mask sert à savoir quels tokens sont du padding pour uniformiser les tailles

In [24]:
flattened_input_ids = [item for sublist in input_ids for item in sublist]
flattened_attention_mask = [item for sublist in attention_mask for item in sublist]
print(overflow_to_sample_mapping)
print(len(overflow_to_sample_mapping))
chunkLabels = []
for i in overflow_to_sample_mapping.tolist():
    chunkLabels.append(labels[i])
grouped_input_ids= []
grouped_attention_mask = []
for i in range(len(chunkLabels)):
    grouped_input_ids.append(flattened_input_ids[i*tokenNumber:(i+1)*tokenNumber])
    grouped_attention_mask.append(flattened_attention_mask[i*tokenNumber:(i+1)*tokenNumber])
print(len(grouped_input_ids))

tensor([ 0,  1,  1,  2,  3,  4,  4,  5,  6,  7,  8,  8,  9,  9, 10, 11, 11, 12,
        13, 13, 14, 15, 16, 17, 17, 18, 19, 20, 21, 21, 21, 22, 22, 23, 23, 23,
        24, 25, 26, 26, 27, 27, 28, 28, 28, 29, 29, 29, 30, 30, 31, 32, 33, 34,
        35, 35, 36, 37, 38, 39, 40, 40, 41, 42, 43, 43, 44, 45, 46, 47, 48, 49,
        50, 51, 52, 52, 53, 53, 53, 54, 55, 56, 57, 58, 59, 59, 60, 60, 61, 61,
        62, 63, 64, 65, 65, 66, 67, 68, 69, 69, 70, 70, 70, 71, 72, 73, 73, 74,
        75, 76, 77, 78, 78, 79, 79, 79, 79, 80, 81, 82, 82, 83, 83, 84, 84, 85,
        86, 87, 87, 87, 87, 88, 89, 90, 91, 92, 92, 92, 93, 94, 95, 96, 96, 97,
        97, 98, 99])
147
147


In [25]:
x_train, x_test, y_train, y_test,x_train_mask, x_test_mask = train_test_split(grouped_input_ids, chunkLabels, grouped_attention_mask, test_size=0.2, random_state=42)

In [ ]:
import torch
class NewsDataset(torch.utils.data.Dataset):
    def __init__(self, input_ids, attention_mask, labels):
        self.input_ids = input_ids
        self.attention_mask = attention_mask
        self.labels = labels

    def __getitem__(self, idx):
        return {
            'input_ids': torch.tensor(self.input_ids[idx]),
            'attention_mask': torch.tensor(self.attention_mask[idx]),
            'labels': torch.tensor(self.labels[idx]),
        }

    def __len__(self):
        return len(self.labels)

train_dataset = NewsDataset(x_train, x_train_mask, y_train)
test_dataset = NewsDataset(x_test, x_test_mask, y_test)
print(train_dataset.input_ids)
print(x_train)

[[tensor(0), tensor(19058), tensor(5), tensor(1562), tensor(977), tensor(50140), tensor(50118), tensor(1121), tensor(2048), tensor(18281), tensor(32165), tensor(5965), tensor(50118), tensor(5521), tensor(1580), tensor(6), tensor(3163), tensor(272), tensor(7586), tensor(20804), tensor(293), tensor(8686), tensor(50118), tensor(12789), tensor(33395), tensor(257), tensor(4270), tensor(452), tensor(137), tensor(5), tensor(446), tensor(50118), tensor(771), tensor(4113), tensor(8), tensor(27088), tensor(1674), tensor(7), tensor(1198), tensor(12), tensor(50118), tensor(19530), tensor(10), tensor(2247), tensor(6221), tensor(136), tensor(455), tensor(582), tensor(50118), tensor(1757), tensor(9), tensor(5), tensor(7944), tensor(4), tensor(50140), tensor(50118), tensor(894), tensor(373), tensor(2298), tensor(852), tensor(22), tensor(102), tensor(22189), tensor(50118), tensor(8490), tensor(113), tensor(8), tensor(26), tensor(350), tensor(203), tensor(3992), tensor(21), tensor(50118), tensor(462), t

In [33]:
from transformers import Trainer, TrainingArguments
from sklearn.metrics import accuracy_score, precision_recall_fscore_support

def compute_metrics(pred):
    labels = pred.label_ids
    preds = pred.predictions.argmax(-1)
    precision, recall, f1, _ = precision_recall_fscore_support(labels, preds, average='weighted')
    acc = accuracy_score(labels, preds)
    return {
        'accuracy': acc,
        'f1': f1,
        'precision': precision,
        'recall': recall
    }   

training_args = TrainingArguments(
    output_dir='./results', 
    num_train_epochs=3, 
    per_device_train_batch_size=4, 
    per_device_eval_batch_size=4,
    logging_dir='./logs',
)


trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
    compute_metrics=compute_metrics
)



In [34]:
trainer.train()

                                      
100%|██████████| 90/90 [06:57<00:00,  4.64s/it]

{'train_runtime': 417.6188, 'train_samples_per_second': 0.84, 'train_steps_per_second': 0.216, 'train_loss': 0.12027729882134332, 'epoch': 3.0}


TrainOutput(global_step=90, training_loss=0.12027729882134332, metrics={'train_runtime': 417.6188, 'train_samples_per_second': 0.84, 'train_steps_per_second': 0.216, 'total_flos': 92352809622528.0, 'train_loss': 0.12027729882134332, 'epoch': 3.0})

In [35]:
results=trainer.evaluate()
print(results)

100%|██████████| 8/8 [00:06<00:00,  1.30it/s]

{'eval_loss': 2.9590868949890137, 'eval_accuracy': 0.6, 'eval_f1': 0.5869989375060368, 'eval_precision': 0.5881944444444444, 'eval_recall': 0.6, 'eval_runtime': 7.3102, 'eval_samples_per_second': 4.104, 'eval_steps_per_second': 1.094, 'epoch': 3.0}


### Tests

Le problème c'est que tu n'a que trois valeurs donc ma maginifique formule pour les corrélations ne fait pas sens pour toi. Dommage.

Donc je t'ai fait une fonction toute neuve. 

FAIRE test du chi2: en gros on répartit l'inflation en quatre grandes catégories selon les quartiles et on regarde le nb d'observations qui se trouvent dans le premier quartile avec perception négative, dans le premier avec perception neutre etc. Tu visualises tout ça grâce à une heatmap. Puis tu fais un test du chi2. 

le carré du rapport de corrélation (eta²). Il exprime la part de la variance de la variable continue “expliquée” par la variable catégorielle et varie entre 0 et 1.
Pour la relation entre une variable catégorielle et une variable continue: la corrélation bisériale ponctuelle mesure l’amplitude de l’écart entre les moyennes de la variable continue selon que l’on appartient ou non à la modalité étudiée. Elle varie entre -1 et 1. Une valeur absolue de 0 indique une absence d’association, une valeur absolue de 1 un association parfaite. Le signe indique le sens de la relation. Mise au carré, la corrélation bisériale ponctuelle peut s’interpréter comme la proportion de variance de la variable continue “expliquée” par l’appartenance à la modalité de la variable catégorielle.

In [ ]:
# Création de la heatmap
# Remplacer var par la variable catégorielle de sentiment
# var1: quartile d'inflation (inf_qu) voir dans quel dataframe tu la copies
# var2: var sentiment
# df: nb de ta table

# Création du tableau croisé
sent_inf=quart_df(inf, freq, 4, 3, var1, var2, df)

# Création de la heatmap
heatmap(
    sent_inf,
    "Sentiments",
    "Inflation",
    "Nb observations",
    "Figure 15: Croisement des quartiles d'inflation (en valeur absolue) et des labels de sentiments"
)


In [ ]:
# Test du chi2
chi_test(sent_inf)

In [ ]:
# Test de corrélation bisériale ponctuelle
# https://docs.scipy.org/doc/scipy/reference/generated/scipy.stats.pointbiserialr.html
# Il faut transformer en variable binaire comme c'est du local: 1 si on est à cette modalité, 0 sinon, pour les trois modalités

pointbiserialr(var1, var2)

In [ ]:
# bon bizarrement le eta ratio n'est pas implémenté en tout cas je l'ai pas trouvé et là je n'ai pas trop le tps
# si tu es mitivé: https://stackoverflow.com/questions/52083501/how-to-compute-correlation-ratio-or-eta-in-python